# Imports

In [1]:
from bs4 import BeautifulSoup as soup
from selenium import webdriver
import json
import pandas as pd
# from selenium.webdriver.common.by import By

In [4]:
import pandas as pd
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options

# Web Driver

In [5]:
chop = webdriver.ChromeOptions()
chop.add_extension('AdGuard AdBlocker 4.1.55.0.crx')
driver = webdriver.Chrome('chromedriver', chrome_options=chop)

<ipython-input-5-6e08d95acc7b>:3: DeprecationWarning: use options instead of chrome_options
  driver = webdriver.Chrome('chromedriver', chrome_options=chop)


WebDriverException: Message: 'chromedriver' executable needs to be in PATH. Please see https://chromedriver.chromium.org/home


In [5]:
url = 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results'
driver.get(url)
# data = page_soup.findAll(
#     "pre", {"style":"word-wrap: break-word; white-space: pre-wrap;"})

In [6]:
html = driver.page_source.encode('utf-8')
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

In [7]:
containers = page_soup.findAll(
    "div", {"class": "ds-p-4"})

In [21]:
containers

[<div class="ds-p-4 hover:ds-bg-ui-fill-translucent ds-border-none ds-border-t ds-border-line"><div class="ds-flex"><div class="ds-text-compact-xs ds-font-bold ds-w-24">Fri, 31 Mar</div><div class="ds-grow ds-px-4 ds-border-r ds-border-line-default-translucent"><a class="ds-no-tap-higlight" href="/series/indian-premier-league-2023-1345038/gujarat-titans-vs-chennai-super-kings-1st-match-1359475/full-scorecard"><div class="ds-text-compact-xxs"><div class=""><div class="ds-flex ds-justify-between ds-items-center"><div class="ds-truncate"><span class=""><span class="ds-text-tight-xs ds-font-bold ds-uppercase ds-leading-5">RESULT</span></span><div class="ds-text-tight-xs ds-truncate ds-text-typo-mid3">1st Match (N), Ahmedabad, March 31, 2023<!-- -->, <span class="ds-cursor-pointer ds-inline-flex ds-items-start ds-leading-none !ds-inline" title="IPL 2023"><span class="ds-text-tight-xs ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-p

# Basic Match Details

In [9]:
data = []

for item in containers:
    json_obj = {}
    try:
        if(item.find('div', attrs={'class': 'ds-text-compact-xs ds-font-bold ds-w-24'})):
            json_obj['date'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[2] + item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[3]
        json_obj['id'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('/match-report', '').split('-')[-1]
        json_obj['description'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text
        if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 0):
            json_obj['team1'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[0].text
        if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 1):
            json_obj['team2'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[1].text
        if(len(item.findAll('strong', attrs={'class': ''})) > 0):
            json_obj['team1_score'] = item.findAll('strong', attrs={'class': ''})[0].text
            json_obj['team1_runs'] = json_obj['team1_score'].split('/')[0]
            if(len(json_obj['team1_score'].split('/'))==1):
                json_obj['team1_wickets'] = '10'
            else:
                json_obj['team1_wickets'] = json_obj['team1_score'].split('/')[1]
        if(len(item.findAll('strong', attrs={'class': ''})) > 1):
            json_obj['team2_score'] = item.findAll('strong', attrs={'class': ''})[1].text
            json_obj['team2_runs'] = json_obj['team2_score'].split('/')[0]
            if(len(json_obj['team2_score'].split('/'))==1):
                json_obj['team2_wickets'] = '10'
            else:
                json_obj['team2_wickets'] = json_obj['team2_score'].split('/')[1]
        json_obj['result'] = item.find('p', attrs={'class': 'ds-text-tight-s ds-font-regular ds-line-clamp-2 ds-text-typo'})['title']
        json_obj['live_score_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','live-cricket-score')
        json_obj['match_overs_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','match-overs-comparison')
        # json_obj['live_score'] = json_obj['live_score'].str.replace('match-report','live-cricket-score')
        data.append(json_obj)
    except:
        # print(e)
        pass

In [10]:
match_pd = pd.DataFrame.from_dict(data)

In [12]:
match_pd.to_csv('2023_matches.csv', index=False)
match_pd

date       id  \
0    March 31 2023  1359475   
1    April 01 2023  1359476   
2    April 01 2023  1359477   
3    April 02 2023  1359478   
4    April 02 2023  1359479   
..             ...      ...   
69     May 21 2023  preview   
70     May 23 2023  1345038   
71     May 24 2023  1345038   
72     May 26 2023  1345038   
73     May 28 2023  1345038   

                                          description  \
0   1st Match (N), Ahmedabad, March 31, 2023, Indi...   
1   2nd Match (D/N), Mohali, April 01, 2023, India...   
2   3rd Match (N), Lucknow, April 01, 2023, Indian...   
3   4th Match (D/N), Hyderabad, April 02, 2023, In...   
4   5th Match (N), Bengaluru, April 02, 2023, Indi...   
..                                                ...   
69  70th Match (N), Bengaluru, May 21, 2023, India...   
70  Qualifier 1 (N), Chennai, May 23, 2023, Indian...   
71  Eliminator (N), Chennai, May 24, 2023, Indian ...   
72  Qualifier 2 (N), Ahmedabad, May 26, 2023, Indi...   
73  Final (N), Ahmedabad, May 28, 2023, Indian Pre...   

                          team1           team2 team1_score team1_runs  \
0                           CSK              GT       178/7        178   
1                          PBKS             KKR       191/5        191   
2                           LSG              DC       193/6        193   
3                            RR             SRH       203/5        203   
4                            MI             RCB       171/7        171   
..                          ...             ...         ...        ...   
69  Royal Challengers Bangalore  Gujarat Titans         NaN        NaN   
70          Chennai Super Kings  Gujarat Titans         NaN        NaN   
71         Lucknow Super Giants             TBA         NaN        NaN   
72                          TBA             TBA         NaN        NaN   
73                          TBA             TBA         NaN        NaN   

   team1_wickets team2_score team2_runs team2_wickets  \
0              7       182/5        182             5   
1              5       146/7        146             7   
2              6       143/9        143             9   
3              5       131/8        131             8   
4              7       172/2        172             2   
..           ...         ...        ...           ...   
69           NaN         NaN        NaN           NaN   
70           NaN         NaN        NaN           NaN   
71           NaN         NaN        NaN           NaN   
72           NaN         NaN        NaN           NaN   
73           NaN         NaN        NaN           NaN   

                                              result  \
0   Titans won by 5 wickets (with 4 balls remaining)   
1            Punjab Kings won by 7 runs (DLS method)   
2                        Super Giants won by 50 runs   
3                              Royals won by 72 runs   
4     RCB won by 8 wickets (with 22 balls remaining)   
..                                               ...   
69                            RCB vs GT - 70th Match   
70                           CSK vs GT - Qualifier 1   
71                           LSG vs TBA - Eliminator   
72                          TBA vs TBA - Qualifier 2   
73                                TBA vs TBA - Final   

                                      live_score_link  \
0   /series/indian-premier-league-2023-1345038/guj...   
1   /series/indian-premier-league-2023-1345038/pun...   
2   /series/indian-premier-league-2023-1345038/luc...   
3   /series/indian-premier-league-2023-1345038/sun...   
4   /series/indian-premier-league-2023-1345038/roy...   
..                                                ...   
69  /series/indian-premier-league-2023-1345038/roy...   
70         /series/indian-premier-league-2023-1345038   
71         /series/indian-premier-league-2023-1345038   
72         /series/indian-premier-league-2023-1345038   
73         /series/indian-premier-league-2023-1345038   

                        

# Match Overs and Toss Details

In [8]:
espncricinfo = "https://www.espncricinfo.com"
data = []
for index, row in match_pd.iterrows():
    url = espncricinfo + row['live_score_link']
    id = row['id']
    team1 = row['team1']
    team2 = row['team2']
    driver.get(url)
    print("Fetched Page", id)
    page_num = 0
    content = driver.page_source
    page_soup = soup(driver.page_source, 'lxml')

    json_obj = {}
    try:
        table = page_soup.find("table", {"class": "ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"})
        match_details = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
    
        json_obj['id'] = id
        json_obj['venue_name'] = match_details[0].text
        json_obj['city'] = match_details[0].text.split(',')[-1]
        json_obj['venue_id'] = table.find("a", {"class": "ds-inline-flex ds-items-start ds-leading-none"})['href'].replace(".html", "").split("/")[-1]
        json_obj['toss_won'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[0]
        if('field' in table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[1]):
            json_obj['decision'] = 'BOWL FIRST'
        else:
            json_obj['decision'] = 'BAT FIRST'
        json_obj['pom'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block ds-ml-2"})[0].text
        json_obj['points'] = table.findAll("span", {"class":"ds-text-tight-s ds-font-regular"})[2].text
        json_obj['super_over'] = "FALSE"
        json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[1].text.split(',')[0].replace("/20 ov", "")
        json_obj['team2_overs'] = json_obj['team2_overs'].replace("(", "").replace(" ov", "").split('/')[0]
        print('team2 overs ', json_obj['team2_overs'])
        json_obj['team1_overs'] = "20"
        if(team1 in json_obj['points'].split(',')[0]):
            json_obj['winner'] = team1
        else:
            json_obj['winner'] = team2

        key_players = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
        json_obj['team1_key_batters'] = key_players[0].text + ', ' + key_players[2].text
        json_obj['team1_key_bowlers'] = key_players[5].text + ', ' + key_players[7].text
        json_obj['team2_key_batters'] = key_players[4].text + ', ' + key_players[6].text
        json_obj['team2_key_bowlers'] = key_players[1].text + ', ' + key_players[3].text
        data.append(json_obj)
        print(len(data))
    except Exception as e:
        pass
        # raise e

match_2_pd = pd.DataFrame.from_dict(data)

NameError: name 'match_pd' is not defined

In [253]:
overall_summary = match_2_pd.join(match_pd.set_index('id'), on='id')

In [257]:
overall_summary_copy = overall_summary.copy()

# Over By Over

In [270]:
espncricinfo = "https://www.espncricinfo.com"
data = []

for index, row in overall_summary_copy.iterrows():
    url = espncricinfo + row['match_overs_link']
    id = row['id']
    try:
        team1_overs = int(float(row['team1_overs']))
    except:
        team1_overs = 0
    try:
        team2_overs = int(float(row['team2_overs']))
    except: 
        team2_overs = 0
    print(team1_overs, team2_overs)
    driver.get(url)
    print("Fetched Page", id)
    page_num = 0
    content = driver.page_source
    page_soup = soup(driver.page_source, 'lxml')

    over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

    all_over_count = 1
    team1_ocount = 1
    team2_ocount = 1
    team1_runs = []
    team1_wickets = []
    team2_runs = []
    team2_wickets = []

    json_obj = {}
    json_obj['id'] = id
    for over in over_details:
        over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
        if ((all_over_count%2==0) and (team2_ocount <= team2_overs)):
            team2_runs.append(over_desc.split(" ")[0])
            team2_wickets.append(over_desc.split(" ")[2])
            team2_ocount += 1
        elif (team1_ocount <= team1_overs):
            team1_runs.append(over_desc.split(" ")[0])
            team1_wickets.append(over_desc.split(" ")[2])
            team1_ocount += 1
        all_over_count += 1

    # team1_runs = [eval(i) for i in team1_runs]
    # team2_runs = [eval(i) for i in team2_runs]
    # team1_wickets = [eval(i) for i in team1_wickets]
    # team2_wickets = [eval(i) for i in team2_wickets]

    print(team1_runs)
    print(team2_runs)
    team1_pp_runs_scored = team1_middle_runs_scored = team1_death_runs_scored = 0
    team1_pp_wickets_lost = team1_middle_wickets_lost = team1_death_wickets_lost = 0

    team2_pp_runs_scored = team2_middle_runs_scored = team2_death_runs_scored = 0
    team2_pp_wickets_lost = team2_middle_wickets_lost = team2_death_wickets_lost = 0

    team1_ocount = 1
    team2_ocount = 1
    
    for i in range(20):
        if i<6:
            if (team1_ocount <= team1_overs):
                team1_pp_runs_scored += int(team1_runs[i])
                team1_pp_wickets_lost += int(team1_wickets[i])
                team1_ocount += 1
            if (team2_ocount <= team2_overs):
                team2_pp_runs_scored += int(team2_runs[i])
                team2_pp_wickets_lost += int(team2_wickets[i])
                team2_ocount += 1
        elif (6<=i<=14):
            if (team1_ocount <= team1_overs):
                team1_middle_runs_scored += int(team1_runs[i])
                team1_middle_wickets_lost += int(team1_wickets[i])
                team1_ocount += 1
            if (team2_ocount <= team2_overs):
                team2_middle_runs_scored += int(team2_runs[i])
                team2_middle_wickets_lost += int(team2_wickets[i])
                team2_ocount += 1
        elif i>14:
            if (team1_ocount <= team1_overs):
                team1_death_runs_scored += int(team1_runs[i])
                team1_death_wickets_lost += int(team1_wickets[i])
                team1_ocount += 1
            if (team2_ocount <= team2_overs):
                team2_death_runs_scored += int(team2_runs[i])
                team2_death_wickets_lost += int(team2_wickets[i])
                team2_ocount += 1

    json_obj['team1_pp_runs_scored'] = team1_pp_runs_scored 
    json_obj['team1_middle_runs_scored'] = team1_middle_runs_scored
    json_obj['team1_death_runs_scored'] = team1_death_runs_scored

    json_obj['team1_pp_wickets_lost'] = team1_pp_wickets_lost
    json_obj['team1_middle_wickets_lost'] = team1_middle_wickets_lost
    json_obj['team1_death_wickets_lost'] = team1_death_wickets_lost

    json_obj['team2_pp_runs_scored'] = team2_pp_runs_scored
    json_obj['team2_middle_runs_scored'] = team2_middle_runs_scored
    json_obj['team2_death_runs_scored'] = team2_death_runs_scored

    json_obj['team2_pp_wickets_lost'] = team2_pp_wickets_lost
    json_obj['team2_middle_wickets_lost'] = team2_middle_wickets_lost
    json_obj['team2_death_wickets_lost'] = team2_death_wickets_lost

    data.append(json_obj)
    print(len(data))
    print(json_obj)
match_3_pd = pd.DataFrame.from_dict(data)

20 19
Fetched Page 1359475
['2', '11', '1', '15', '17', '5', '13', '8', '18', '3', '7', '14', '7', '4', '8', '7', '11', '4', '10', '13']
['3', '15', '11', '12', '15', '9', '6', '11', '7', '4', '13', '5', '3', '13', '11', '7', '4', '7', '15']
1
{'id': '1359475', 'team1_pp_runs_scored': 51, 'team1_middle_runs_scored': 82, 'team1_death_runs_scored': 45, 'team1_pp_wickets_lost': 2, 'team1_middle_wickets_lost': 2, 'team1_death_wickets_lost': 3, 'team2_pp_runs_scored': 65, 'team2_middle_runs_scored': 73, 'team2_death_runs_scored': 33, 'team2_pp_wickets_lost': 1, 'team2_middle_wickets_lost': 3, 'team2_death_wickets_lost': 1}
20 16
Fetched Page 1359476
['9', '14', '1', '12', '14', '6', '13', '10', '12', '9', '9', '12', '8', '13', '1', '10', '11', '4', '8', '15']
['13', '4', '7', '5', '6', '11', '4', '10', '15', '5', '3', '8', '9', '18', '18', '10']
2
{'id': '1359476', 'team1_pp_runs_scored': 56, 'team1_middle_runs_scored': 87, 'team1_death_runs_scored': 48, 'team1_pp_wickets_lost': 1, 'team1_m

In [297]:

overall_summary = match_2_pd.join(match_pd.set_index('id'), on='id')
overall_summary = overall_summary.join(match_3_pd.set_index('id'), on='id')

# Data Cleaning

In [306]:
# os['city'] = os['venue_name'].str.split(',')[0]
osum = overall_summary.copy()
osum = osum.convert_dtypes()

In [307]:
osum.head()

id                                         venue_name         city  \
0  1359475                   Narendra Modi Stadium, Ahmedabad    Ahmedabad   
1  1359476  Punjab Cricket Association IS Bindra Stadium, ...   Chandigarh   
2  1359477  Bharat Ratna Shri Atal Bihari Vajpayee Ekana C...      Lucknow   
3  1359478  Rajiv Gandhi International Stadium, Uppal, Hyd...    Hyderabad   
4  1359479                   M Chinnaswamy Stadium, Bengaluru    Bengaluru   

  venue_id                     toss_won    decision             pom  \
0    57851               Gujarat Titans  BOWL FIRST     Rashid Khan   
1    57991        Kolkata Knight Riders  BOWL FIRST  Arshdeep Singh   
2  1070094               Delhi Capitals  BOWL FIRST       Mark Wood   
3    58142          Sunrisers Hyderabad  BOWL FIRST     Jos Buttler   
4    57897  Royal Challengers Bangalore  BOWL FIRST  Faf du Plessis   

                                            points super_over team2_overs  \
0          Gujarat Titans 2, Chennai Super Kings 0      FALSE        19.2   
1          Punjab Kings 2, Kolkata Knight Riders 0      FALSE          16   
2         Lucknow Super Giants 2, Delhi Capitals 0      FALSE          20   
3        Rajasthan Royals 2, Sunrisers Hyderabad 0      FALSE          20   
4  Royal Challengers Bangalore 2, Mumbai Indians 0      FALSE        16.2   

   ... team1_death_runs_scored team1_pp_wickets_lost  \
0  ...                      45                     2   
1  ...                      48                     1   
2  ...                      66                     1   
3  ...                      43                     1   
4  ...                      58                     3   

  team1_middle_wickets_lost team1_death_wickets_lost team2_pp_runs_scored  \
0                         2                        3                   65   
1                         3                        1                   46   
2                         3                        2                   47   
3                         2                        2                   30   
4                         2                        2                   53   

  team2_middle_runs_scored team2_death_runs_scored team2_pp_wickets_lost  \
0                       73                      33                     1   
1                       90                      10                     3   
2                       63                      33                     2   
3                       55                      46                     2   
4                       95                      13                     0   

  team2_middle_wickets_lost team2_death_wickets_lost  
0                         3                        1  
1                         3                        1  
2                         3                        4  
3                         5                        1  
4                         1                        1  

[5 rows x 41 columns]

In [312]:
venue_dict = {' Ahmedabad':'GT', ' Chandigarh':'KXIP', ' Lucknow':'LSG', ' Hyderabad': 'SRH', ' Mumbai':'MI', ' Bengaluru': 'RCB', ' Chennai': 'CSK', ' Kolkata': 'KKR', ' Jaipur':'RR', ' Delhi':'DC', ' Guwahati':'RR'}

In [313]:
osum['home_team'] = osum['city']
osum.replace({'home_team': venue_dict}, inplace=True)

In [314]:
osum['home_team'].unique()

array(['GT', 'KXIP', 'LSG', 'SRH', 'RCB', 'CSK', 'DC', 'RR', 'MI', 'KKR'],
      dtype=object)

In [315]:
osum.columns

Index(['id', 'venue_name', 'city', 'venue_id', 'toss_won', 'decision', 'pom',
       'points', 'super_over', 'team2_overs', 'team1_overs', 'winner',
       'team1_key_batters', 'team1_key_bowlers', 'team2_key_batters',
       'team2_key_bowlers', 'date', 'description', 'team1', 'team2',
       'team1_score', 'team1_runs', 'team1_wickets', 'team2_score',
       'team2_runs', 'team2_wickets', 'result', 'live_score_link',
       'match_overs_link', 'team1_pp_runs_scored', 'team1_middle_runs_scored',
       'team1_death_runs_scored', 'team1_pp_wickets_lost',
       'team1_middle_wickets_lost', 'team1_death_wickets_lost',
       'team2_pp_runs_scored', 'team2_middle_runs_scored',
       'team2_death_runs_scored', 'team2_pp_wickets_lost',
       'team2_middle_wickets_lost', 'team2_death_wickets_lost', 'home_team'],
      dtype='object')

In [322]:
osum.away_team.unique()

array(['CSK', 'KKR', 'DC', 'RR', 'MI', 'LSG', 'GT', 'KXIP', 'SRH', 'RCB'],
      dtype=object)

In [317]:
osum.replace({'team1': {'PBKS':'KXIP'}, 'team2':{'PBKS':'KXIP'}}, inplace=True)

In [318]:
osum['super_over'] = 'FALSE'

In [320]:
osum['away_team'] = osum.apply(lambda x: x['team2'] if x['team1']==x['home_team'] else x['team1'], axis=1)

In [324]:
osum['home_overs'] = osum.apply(lambda x: x['team1_overs'] if x['team1']==x['home_team'] else x['team2_overs'], axis=1)
osum['home_runs'] = osum.apply(lambda x: x['team1_runs'] if x['team1']==x['home_team'] else x['team2_runs'], axis=1)
osum['home_wickets'] = osum.apply(lambda x: x['team1_wickets'] if x['team1']==x['home_team'] else x['team2_wickets'], axis=1)
osum['home_key_batter'] = osum.apply(lambda x: x['team1_key_batters'] if x['team1']==x['home_team'] else x['team2_key_batters'], axis=1)
osum['home_key_bowler'] = osum.apply(lambda x: x['team1_key_bowlers'] if x['team1']==x['home_team'] else x['team2_key_bowlers'], axis=1)

osum['away_overs'] = osum.apply(lambda x: x['team1_overs'] if x['team1']==x['away_team'] else x['team2_overs'], axis=1)
osum['away_runs'] = osum.apply(lambda x: x['team1_runs'] if x['team1']==x['away_team'] else x['team2_runs'], axis=1)
osum['away_wickets'] = osum.apply(lambda x: x['team1_wickets'] if x['team1']==x['away_team'] else x['team2_wickets'], axis=1)
osum['away_key_batter'] = osum.apply(lambda x: x['team1_key_batters'] if x['team1']==x['away_team'] else x['team2_key_batters'], axis=1)
osum['away_key_bowler'] = osum.apply(lambda x: x['team1_key_bowlers'] if x['team1']==x['away_team'] else x['team2_key_bowlers'], axis=1)

In [334]:
osum['home_pp_runs_scored'] = osum.apply(lambda x: x['team1_pp_runs_scored'] if x['team1']==x['home_team'] else x['team2_pp_runs_scored'], axis=1)
osum['home_middle_runs_scored'] = osum.apply(lambda x: x['team1_middle_runs_scored'] if x['team1']==x['home_team'] else x['team2_middle_runs_scored'], axis=1)
osum['home_death_runs_scored'] = osum.apply(lambda x: x['team1_death_runs_scored'] if x['team1']==x['home_team'] else x['team2_death_runs_scored'], axis=1)

osum['home_pp_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['middle_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['death_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)

osum['away_pp_runs_scored'] = osum.apply(lambda x: x['team1_pp_runs_scored'] if x['team1']==x['away_team'] else x['team2_pp_runs_scored'], axis=1)
osum['away_middle_runs_scored'] = osum.apply(lambda x: x['team1_middle_runs_scored'] if x['team1']==x['away_team'] else x['team2_middle_runs_scored'], axis=1)
osum['away_death_runs_scored'] = osum.apply(lambda x: x['team1_death_runs_scored'] if x['team1']==x['away_team'] else x['team2_death_runs_scored'], axis=1)

osum['away_pp_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['away_middle_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['away_death_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)

In [327]:
team_long_names = {'Gujarat Titans': 'GT', 'Kolkata Knight Riders': 'KKR', 'Delhi Capitals':'DC', 'Sunrisers Hyderabad':'SRH', 
'Royal Challengers Bangalore':'RCB', 'Lucknow Super Giants': 'LSG', 'Rajasthan Royals':'RR', 'Chennai Super Kings':'CSK', 'Punjab Kings':'KXIP', 'Mumbai Indians':'MI'}

In [328]:
osum.replace({'toss_won':team_long_names}, inplace=True)

In [329]:
osum.toss_won.unique()

array(['GT', 'KKR', 'DC', 'SRH', 'RCB', 'LSG', 'RR', 'CSK', 'KXIP', 'MI'],
      dtype=object)

In [330]:
osum.head()

id                                         venue_name         city  \
0  1359475                   Narendra Modi Stadium, Ahmedabad    Ahmedabad   
1  1359476  Punjab Cricket Association IS Bindra Stadium, ...   Chandigarh   
2  1359477  Bharat Ratna Shri Atal Bihari Vajpayee Ekana C...      Lucknow   
3  1359478  Rajiv Gandhi International Stadium, Uppal, Hyd...    Hyderabad   
4  1359479                   M Chinnaswamy Stadium, Bengaluru    Bengaluru   

  venue_id toss_won    decision             pom  \
0    57851       GT  BOWL FIRST     Rashid Khan   
1    57991      KKR  BOWL FIRST  Arshdeep Singh   
2  1070094       DC  BOWL FIRST       Mark Wood   
3    58142      SRH  BOWL FIRST     Jos Buttler   
4    57897      RCB  BOWL FIRST  Faf du Plessis   

                                            points super_over team2_overs  \
0          Gujarat Titans 2, Chennai Super Kings 0      FALSE        19.2   
1          Punjab Kings 2, Kolkata Knight Riders 0      FALSE          16   
2         Lucknow Super Giants 2, Delhi Capitals 0      FALSE          20   
3        Rajasthan Royals 2, Sunrisers Hyderabad 0      FALSE          20   
4  Royal Challengers Bangalore 2, Mumbai Indians 0      FALSE        16.2   

   ... home_overs home_runs home_wickets                      home_key_batter  \
0  ...       19.2       182            5        Shubman Gill , Vijay Shankar    
1  ...         20       191            5  Bhanuka Rajapaksa , Shikhar Dhawan    
2  ...         20       193            6       Kyle Mayers , Nicholas Pooran    
3  ...         20       131            8       Abdul Samad *, Mayank Agarwal    
4  ...       16.2       172            2       Virat Kohli *, Faf du Plessis    

                 home_key_bowler away_overs away_runs away_wickets  \
0    Rashid Khan, Mohammed Shami         20       178            7   
1   Arshdeep Singh, Rahul Chahar         16       146            7   
2          Mark Wood, Avesh Khan         20       143            9   
3  T Natarajan, Fazalhaq Farooqi         20       203            5   
4    Karn Sharma, Mohammed Siraj         20       171            7   

                   away_key_batter                          away_key_bowler  
0     Ruturaj Gaikwad , Moeen Ali   Rajvardhan Hangargekar, Ravindra Jadeja  
1  Andre Russell , Venkatesh Iyer           Tim Southee, Varun Chakravarthy  
2    David Warner , Rilee Rossouw            Khaleel Ahmed, Chetan Sakariya  
3      Sanju Samson , Jos Buttler             Yuzvendra Chahal, Trent Boult  
4    Tilak Varma *, Nehal Wadhera                Arshad Khan, Cameron Green  

[5 rows x 53 columns]

In [331]:
osum.columns

Index(['id', 'venue_name', 'city', 'venue_id', 'toss_won', 'decision', 'pom',
       'points', 'super_over', 'team2_overs', 'team1_overs', 'winner',
       'team1_key_batters', 'team1_key_bowlers', 'team2_key_batters',
       'team2_key_bowlers', 'date', 'description', 'team1', 'team2',
       'team1_score', 'team1_runs', 'team1_wickets', 'team2_score',
       'team2_runs', 'team2_wickets', 'result', 'live_score_link',
       'match_overs_link', 'team1_pp_runs_scored', 'team1_middle_runs_scored',
       'team1_death_runs_scored', 'team1_pp_wickets_lost',
       'team1_middle_wickets_lost', 'team1_death_wickets_lost',
       'team2_pp_runs_scored', 'team2_middle_runs_scored',
       'team2_death_runs_scored', 'team2_pp_wickets_lost',
       'team2_middle_wickets_lost', 'team2_death_wickets_lost', 'home_team',
       'away_team', 'home_overs', 'home_runs', 'home_wickets',
       'home_key_batter', 'home_key_bowler', 'away_overs', 'away_runs',
       'away_wickets', 'away_key_batter', 'aw

In [344]:
os_copy = osum.drop(['team2_overs', 'team1_overs', 'winner',
       'team1_key_batters', 'team1_key_bowlers', 'team2_key_batters',
       'team2_key_bowlers', 'date', 'description', 'team1', 'team2',
       'team1_runs', 'team1_wickets', 'team2_runs', 'team2_wickets', 'result', 'live_score_link',
       'match_overs_link', 'team1_pp_runs_scored', 'team1_middle_runs_scored',
       'team1_death_runs_scored', 'team1_pp_wickets_lost',
       'team1_middle_wickets_lost', 'team1_death_wickets_lost',
       'team2_pp_runs_scored', 'team2_middle_runs_scored',
       'team2_death_runs_scored', 'team2_pp_wickets_lost',
       'team2_middle_wickets_lost', 'team2_death_wickets_lost'], axis=1)
os_copy.rename(columns={'team1_score':'1st_innings_score', 'team2_score':'2nd_innings_score'},inplace=True)

In [345]:
os_copy.columns

Index(['id', 'venue_name', 'city', 'venue_id', 'toss_won', 'decision', 'pom',
       'points', 'super_over', '1st_innings_score', '2nd_innings_score',
       'home_team', 'away_team', 'home_overs', 'home_runs', 'home_wickets',
       'home_key_batter', 'home_key_bowler', 'away_overs', 'away_runs',
       'away_wickets', 'away_key_batter', 'away_key_bowler',
       'home_pp_runs_scored', 'home_middle_runs_scored',
       'home_death_runs_scored', 'home_pp_wickets_lost', 'middle_wickets_lost',
       'death_wickets_lost', 'away_pp_runs_scored', 'away_middle_runs_scored',
       'away_death_runs_scored', 'away_pp_wickets_lost',
       'away_middle_wickets_lost', 'away_death_wickets_lost'],
      dtype='object')

In [346]:
os_copy.to_csv('2023_overall_summary.csv', index=False)

# Sample Trials

In [476]:
# url = 'https://www.espncricinfo.com/series/pepsi-indian-premier-league-2015-791129/kings-xi-punjab-vs-royal-challengers-bangalore-50th-match-829803/live-cricket-score'
url = 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/lucknow-super-giants-vs-chennai-super-kings-45th-match-1359519/live-cricket-score'
driver.get(url)

In [477]:
html = driver.page_source.encode('utf-8')
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

In [478]:
page_soup

<html lang="en"><head><script async="" data-jsonpid="" src="https://cdn-gl.imrworldwide.com/novms/js/2/nlsSDK600.bundle.min.js"></script><script async="" src="https://cdn-gl.imrworldwide.com/conf/PED8CDAC2-F114-41BE-8B98-AFA06FAEA06E.js#name=nlsnInstance&amp;ns=NOLBUNDLE"></script><script async="async" charset="UTF-8" src="https://cdn.taboola.com/libtrc/share-buttons-detection.20230516-18_b6-PR-56640-DEV-129605-vignette-visibility-after-fixing-the-visibility-state-in-rbox-c4cbb2e8872.es6.js" type="text/javascript"></script><script async="async" charset="UTF-8" src="https://cdn.taboola.com/libtrc/article-detection.20230516-18_b6-PR-56640-DEV-129605-vignette-visibility-after-fixing-the-visibility-state-in-rbox-c4cbb2e8872.es6.js" type="text/javascript"></script><script async="async" charset="UTF-8" src="https://cdn.taboola.com/libtrc/distance-from-article.20230516-18_b6-PR-56640-DEV-129605-vignette-visibility-after-fixing-the-visibility-state-in-rbox-c4cbb2e8872.es6.js" type="text/javasc

In [482]:
page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"})[0].text.replace("(", "").split(' ')[0]

'19.2'

In [369]:
page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})

''

In [ ]:
json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[1].text.split(',')[0].replace("/20 ov", "")
json_obj['team2_overs'] = json_obj['team2_overs'].replace("(", "").replace(" ov", "").split('/')[0]
print('team2 overs ', json_obj['team2_overs'])
json_obj['team1_overs'] = "20"

In [115]:
table = page_soup.find("table", {"class": "ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"})
match_details = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})

In [117]:
table

<table class="ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"><tbody class=""><tr class=""><td class="ds-min-w-max" colspan="2"><a class="ds-inline-flex ds-items-start ds-leading-none" href="https://www.espncricinfo.com/ci/content/ground/57851.html"><span class="ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block">Narendra Modi Stadium, Ahmedabad</span></a></td></tr><tr class=""><td class="ds-min-w-max ds-border-r ds-border-line"><span class="ds-text-tight-s ds-font-medium">Toss</span></td><td class="ds-min-w-max"><span class="ds-text-tight-s ds-font-regular">Gujarat Titans, elected to field first</span></td></tr><tr class=""><td class="ds-min-w-max ds-border-r ds-border-line"><span class="ds-text-tight-s ds-font-medium">Series</span></td><td class="ds-min-w-max"><div class=""><a class="ds-inline-flex ds-items-start ds-leading-none" href="/series/indian-pre

In [124]:
json_obj = {}
try:
    json_obj['venue_name'] = match_details[0].text
    json_obj['venue_id'] = table.find("a", {"class": "ds-inline-flex ds-items-start ds-leading-none"})['href'].replace(".html", "").split("/")[-1]
    json_obj['toss_won'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[0]
    if('field' in table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[1]):
        json_obj['decision'] = 'BOWL FIRST'
    else:
        json_obj['decision'] = 'BAT FIRST'
    json_obj['pom'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block ds-ml-2"})[0].text
    json_obj['points'] = table.findAll("span", {"class":"ds-text-tight-s ds-font-regular"})[2].text
    json_obj['super_over'] = "FALSE"
    json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[1].text.split(',')[0].replace("/20 ov", "")
    json_obj['team2_overs'] = json_obj['team2_overs'].replace("(", "")
    json_obj['team1_overs'] = "20"
    data.append(json_obj)
except:
    pass

In [125]:
json_obj

{'venue_name': 'Narendra Modi Stadium, Ahmedabad',
 'venue_id': '57851',
 'toss_won': 'Gujarat Titans',
 'decision': 'BOWL FIRST',
 'pom': 'Rashid Khan',
 'points': 'Gujarat Titans 2, Chennai Super Kings 0',
 'super_over': 'FALSE',
 'team2_overs': '19.2',
 'team1_overs': '20'}

In [141]:
url = "https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/gujarat-titans-vs-chennai-super-kings-1st-match-1359475/match-overs-comparison"
driver.get(url)

In [467]:
url = 'https://www.espncricinfo.com/series/ipl-2016-968923/gujarat-lions-vs-kolkata-knight-riders-51st-match-981001/live-cricket-score'
driver.get(url)

In [468]:
html = driver.page_source.encode('utf-8')
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

In [469]:
page_soup

<html lang="en"><head><script async="async" charset="UTF-8" src="https://cdn.taboola.com/scripts/fraud-detect.js" type="text/javascript"></script><script async="async" charset="UTF-8" src="https://cdn.taboola.com/scripts/cds-pips.js" type="text/javascript"></script><script async="" data-jsonpid="" src="https://cdn-gl.imrworldwide.com/novms/js/2/nlsSDK600.bundle.min.js"></script><script async="" src="https://cdn-gl.imrworldwide.com/conf/PED8CDAC2-F114-41BE-8B98-AFA06FAEA06E.js#name=nlsnInstance&amp;ns=NOLBUNDLE"></script><script async="async" charset="UTF-8" src="https://cdn.taboola.com/libtrc/share-buttons-detection.20230516-18_b6-PR-56640-DEV-129605-vignette-visibility-after-fixing-the-visibility-state-in-rbox-c4cbb2e8872.es6.js" type="text/javascript"></script><script async="async" charset="UTF-8" src="https://cdn.taboola.com/libtrc/article-detection.20230516-18_b6-PR-56640-DEV-129605-vignette-visibility-after-fixing-the-visibility-state-in-rbox-c4cbb2e8872.es6.js" type="text/javascr

In [143]:
overs = page_soup.findAll(
    "table", {"class": "ds-w-full ds-table ds-table-md ds-table-bordered ds-border-collapse ds-border ds-border-line ds-table-fixed"})


In [151]:
over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

In [163]:
all_over_count = 1
inning_over_count = 1
team1_runs = []
team1_wickets = []
team2_runs = []
team2_wickets = []
for over in over_details:
    over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
    if (all_over_count%2):
        team1_runs.append(over_desc.split(" ")[0])
        team1_wickets.append(over_desc.split(" ")[2])
    else:
        team2_runs.append(over_desc.split(" ")[0])
        team2_wickets.append(over_desc.split(" ")[2])
    all_over_count += 1

In [458]:
url = 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/mumbai-indians-vs-kolkata-knight-riders-22nd-match-1359496/live-cricket-score'
driver.get(url)
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

json_obj = {}
table = page_soup.find("table", {"class": "ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"})
match_details = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[1].text.split(',')[0].replace("/20 ov", "").replace("(", "").replace(" ov", "").split('/')[0]
# json_obj['team2_overs'] = json_obj['team2_overs'].replace("(", "").replace(" ov", "").split('/')[0]
if (page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[0].text==''):
    json_obj['team1_overs'] = "20"
else:
    json_obj['team1_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[0].text.split(',')[0].replace("/20 ov", "").replace("(", "").replace(" ov", "").split('/')[0]

print('team2 overs: ', json_obj['team2_overs'], 'team1 overs: ', json_obj['team1_overs'])

team2 overs:  17.4 team1 overs:  20


In [ ]:
url = 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/mumbai-indians-vs-kolkata-knight-riders-22nd-match-1359496/match-overs-comparison'
id = row['id']
driver.get(url)
# print("Fetched Page", id)
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

try:
    team1_overs
except:
    team1_overs = 0
try:
    team2_overs = int(float(json_obj['team2_overs'])) + 1
except: 
    team2_overs = 18
# print('team2 overs: ', json_obj['team2_overs'], 'team1 overs: ', json_obj['team1_overs'])

all_over_count = 1
team1_ocount = 1
team2_ocount = 1
team1_runs = []
team1_wickets = []
team2_runs = []
team2_wickets = []

for over in over_details:
    over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
    if ((all_over_count%2==0) and (team2_ocount <= team2_overs)):
        team2_runs.append(over_desc.split(" ")[0])
        team2_wickets.append(over_desc.split(" ")[2])
        team2_ocount += 1
    elif (team1_ocount <= team1_overs):
        team1_runs.append(over_desc.split(" ")[0])
        team1_wickets.append(over_desc.split(" ")[2])
        team1_ocount += 1
    all_over_count += 1

# team1_runs = [eval(i) for i in team1_runs]
# team2_runs = [eval(i) for i in team2_runs]
# team1_wickets = [eval(i) for i in team1_wickets]
# team2_wickets = [eval(i) for i in team2_wickets]

print(team1_runs)
print(team2_runs)
print(team1_wickets)
print(team2_wickets)
team1_pp_runs_scored = team1_middle_runs_scored = team1_death_runs_scored = 0
team1_pp_wickets_lost = team1_middle_wickets_lost = team1_death_wickets_lost = 0

team2_pp_runs_scored = team2_middle_runs_scored = team2_death_runs_scored = 0
team2_pp_wickets_lost = team2_middle_wickets_lost = team2_death_wickets_lost = 0

team1_ocount = 1
team2_ocount = 1

for i in range(20):
    if i<6:
        if (team1_ocount <= team1_overs):
            team1_pp_runs_scored += int(team1_runs[i])
            team1_pp_wickets_lost += int(team1_wickets[i])
            team1_ocount += 1
        if (team2_ocount <= team2_overs):
            team2_pp_runs_scored += int(team2_runs[i])
            team2_pp_wickets_lost += int(team2_wickets[i])
            team2_ocount += 1
    elif (6<=i<=14):
        if (team1_ocount <= team1_overs):
            team1_middle_runs_scored += int(team1_runs[i])
            team1_middle_wickets_lost += int(team1_wickets[i])
            team1_ocount += 1
        if (team2_ocount <= team2_overs):
            team2_middle_runs_scored += int(team2_runs[i])
            team2_middle_wickets_lost += int(team2_wickets[i])
            team2_ocount += 1
    elif i>14:
        if (team1_ocount <= team1_overs):
            team1_death_runs_scored += int(team1_runs[i])
            team1_death_wickets_lost += int(team1_wickets[i])
            team1_ocount += 1
        if (team2_ocount <= team2_overs):
            team2_death_runs_scored += int(team2_runs[i])
            team2_death_wickets_lost += int(team2_wickets[i])
            team2_ocount += 1

json_obj['team1_pp_runs_scored'] = team1_pp_runs_scored 
json_obj['team1_middle_runs_scored'] = team1_middle_runs_scored
json_obj['team1_death_runs_scored'] = team1_death_runs_scored

json_obj['team1_pp_wickets_lost'] = team1_pp_wickets_lost
json_obj['team1_middle_wickets_lost'] = team1_middle_wickets_lost
json_obj['team1_death_wickets_lost'] = team1_death_wickets_lost

json_obj['team2_pp_runs_scored'] = team2_pp_runs_scored
json_obj['team2_middle_runs_scored'] = team2_middle_runs_scored
json_obj['team2_death_runs_scored'] = team2_death_runs_scored

json_obj['team2_pp_wickets_lost'] = team2_pp_wickets_lost
json_obj['team2_middle_wickets_lost'] = team2_middle_wickets_lost
json_obj['team2_death_wickets_lost'] = team2_death_wickets_lost


print(json_obj)

In [451]:
team2_wickets

['0',
 '0',
 '0',
 '0',
 '0',
 '1',
 '0',
 '1',
 '0',
 '0',
 '0',
 '0',
 '0',
 '1',
 '0',
 '0',
 '1',
 '1']

In [726]:
url = 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/punjab-kings-vs-lucknow-super-giants-38th-match-1359512/match-overs-comparison'
# id = row['id']
# if(len(row['team1_overs'].split('.'))==2):
#     extra_one = 1
# else:
#     extra_one = 0

# if(len(row['team2_overs'].split('.'))==2):
#     extra_two = 1
# else:
#     extra_two = 0

# try:
#     team1_overs = min(int(float(row['team1_overs'])) + extra_one, 20)
# except:
#     team1_overs = 0
# try:
#     team2_overs = min(int(float(row['team2_overs'])) + extra_two, 20)
# except: 
#     team2_overs = 0
driver.get(url)
# print("Fetched Page", id)
page_num = 0
data =[]
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

all_over_count = 1
team1_ocount = 1
team2_ocount = 1
team1_runs = []
team1_wickets = []
team2_runs = []
team2_wickets = []
team1_overs = 20
team2_overs = 20

json_obj = {}
json_obj['id'] = id
for over in over_details:
    over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
    if ((all_over_count%2==0) and (team2_ocount <= team2_overs)):
        team2_runs.append(over_desc.split(" ")[0])
        team2_wickets.append(over_desc.split(" ")[2])
        team2_ocount += 1
    elif (team1_ocount <= team1_overs):
        team1_runs.append(over_desc.split(" ")[0])
        team1_wickets.append(over_desc.split(" ")[2])
        team1_ocount += 1
    all_over_count += 1

# team1_runs = [eval(i) for i in team1_runs]
# team2_runs = [eval(i) for i in team2_runs]
# team1_wickets = [eval(i) for i in team1_wickets]
# team2_wickets = [eval(i) for i in team2_wickets]

# print('Actual Overs', row['team1_overs'], row['team2_overs'])
print('team1_overs',team1_overs, 'team2_overs', team2_overs)
print('team1_runs',team1_runs)
print('team2_runs',team2_runs)
print('team1_wickets',team1_wickets)
print('team2_wickets',team2_wickets)
team1_pp_runs_scored = team1_middle_runs_scored = team1_death_runs_scored = 0
team1_pp_wickets_lost = team1_middle_wickets_lost = team1_death_wickets_lost = 0

team2_pp_runs_scored = team2_middle_runs_scored = team2_death_runs_scored = 0
team2_pp_wickets_lost = team2_middle_wickets_lost = team2_death_wickets_lost = 0

team1_ocount = 1
team2_ocount = 1

for i in range(20):
    if i<6:
        if (team1_ocount <= team1_overs):
            team1_pp_runs_scored += int(team1_runs[i])
            team1_pp_wickets_lost += int(team1_wickets[i])
            team1_ocount += 1
        if (team2_ocount <= team2_overs):
            team2_pp_runs_scored += int(team2_runs[i])
            team2_pp_wickets_lost += int(team2_wickets[i])
            team2_ocount += 1
    elif (6<=i<=14):
        if (team1_ocount <= team1_overs):
            team1_middle_runs_scored += int(team1_runs[i])
            team1_middle_wickets_lost += int(team1_wickets[i])
            team1_ocount += 1
        if (team2_ocount <= team2_overs):
            team2_middle_runs_scored += int(team2_runs[i])
            team2_middle_wickets_lost += int(team2_wickets[i])
            team2_ocount += 1
    elif i>14:
        if (team1_ocount <= team1_overs):
            team1_death_runs_scored += int(team1_runs[i])
            team1_death_wickets_lost += int(team1_wickets[i])
            team1_ocount += 1
        if (team2_ocount <= team2_overs):
            team2_death_runs_scored += int(team2_runs[i])
            team2_death_wickets_lost += int(team2_wickets[i])
            team2_ocount += 1

json_obj['team1_pp_runs_scored'] = team1_pp_runs_scored 
json_obj['team1_middle_runs_scored'] = team1_middle_runs_scored
json_obj['team1_death_runs_scored'] = team1_death_runs_scored

if(team1_overs>0):
    json_obj['team1_pp_run_rate'] = team1_pp_runs_scored/min(team1_overs, 6)
else:
    json_obj['team1_pp_run_rate']
if(team1_overs>6):
    json_obj['team1_middle_run_rate'] = team1_middle_runs_scored/min(team1_overs-6, 9)
else:
    json_obj['team1_middle_run_rate'] = 0
if(team2_overs>15):
    json_obj['team1_death_run_rate'] = team1_death_runs_scored/min(team1_overs-15, 5)
else:
    json_obj['team1_death_run_rate'] = 0

json_obj['team1_pp_wickets_lost'] = team1_pp_wickets_lost
json_obj['team1_middle_wickets_lost'] = team1_middle_wickets_lost
json_obj['team1_death_wickets_lost'] = team1_death_wickets_lost

json_obj['team2_pp_runs_scored'] = team2_pp_runs_scored
json_obj['team2_middle_runs_scored'] = team2_middle_runs_scored
json_obj['team2_death_runs_scored'] = team2_death_runs_scored

if(team2_overs>0):
    json_obj['team2_pp_run_rate'] = team2_pp_runs_scored/min(team2_overs, 6)
else:
    json_obj['team2_pp_run_rate']
if(team2_overs>6):
    json_obj['team2_middle_run_rate'] = team2_middle_runs_scored/min(team2_overs-6, 9)
else:
    json_obj['team2_middle_run_rate'] = 0
if(team2_overs>15):
    json_obj['team2_death_run_rate'] = team2_death_runs_scored/min(team2_overs-15, 5)
else:
    json_obj['team2_death_run_rate'] = 0

json_obj['team2_pp_wickets_lost'] = team2_pp_wickets_lost
json_obj['team2_middle_wickets_lost'] = team2_middle_wickets_lost
json_obj['team2_death_wickets_lost'] = team2_death_wickets_lost

data.append(json_obj)
print("Match", len(data), "Over-wise done")
print(json_obj)

team1_overs 20 team2_overs 20
team1_runs ['2', '17', '16', '10', '17', '12', '9', '24', '4', '17', '8', '11', '9', '19', '9', '16', '16', '19', '10', '12']
team2_runs ['3', '4', '19', '5', '16', '8', '15', '6', '8', '9', '13', '12', '9', '13', '12', '14', '12', '15', '6', '2']
team1_wickets ['0', '0', '0', '1', '0', '1', '0', '0', '0', '0', '0', '0', '0', '1', '0', '0', '0', '0', '1', '1']
team2_wickets ['1', '0', '0', '1', '0', '0', '0', '0', '0', '0', '0', '1', '1', '0', '0', '1', '1', '2', '1', '1']
Match 1 Over-wise done
{'id': '336040', 'team1_pp_runs_scored': 74, 'team1_middle_runs_scored': 110, 'team1_death_runs_scored': 73, 'team1_pp_run_rate': 12.333333333333334, 'team1_middle_run_rate': 12.222222222222221, 'team1_death_run_rate': 14.6, 'team1_pp_wickets_lost': 2, 'team1_middle_wickets_lost': 1, 'team1_death_wickets_lost': 2, 'team2_pp_runs_scored': 55, 'team2_middle_runs_scored': 97, 'team2_death_runs_scored': 49, 'team2_pp_run_rate': 9.166666666666666, 'team2_middle_run_rate

# All Seasons

In [4]:
chop = webdriver.ChromeOptions()
chop.add_extension('AdGuard AdBlocker 4.1.55.0.crx')
driver = webdriver.Chrome('chromedriver', chrome_options=chop)

<ipython-input-4-6e08d95acc7b>:3: DeprecationWarning: use options instead of chrome_options
  driver = webdriver.Chrome('chromedriver', chrome_options=chop)


In [376]:
url = 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results'
driver.get(url)
# data = page_soup.findAll(
#     "pre", {"style":"word-wrap: break-word; white-space: pre-wrap;"})

In [ ]:
html = driver.page_source.encode('utf-8')
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

Hover Over IPL 2023 Button on Top Left

In [361]:
all_seasons_dump = page_soup.findAll("a", {"class":"ds-cursor-pointer ds-inline-flex ds-items-center ds-w-full ds-py-1.5 ds-text-tight-m ds-px-4 ds-bg-ui-fill ds-text-typo ds-flex ds-items-center ds-box-border hover:ds-bg-ui-fill-hover active:ds-bg-ui-fill-primary active:ds-text-raw-white focus:ds-border focus:ds-border-ui-stroke-primary focus:ds-outline-none"})
all_seasons = {}
for item in all_seasons_dump:
    year = item.text.split(" ")[-1]
    link = item['href']
    print(year)
    all_seasons[year] = link

2022
2021
2020/21
2019
2018
2017
2016
2015
2014
2013
2012
2011
2009/10
2009
2007/08


In [362]:
all_seasons

{'2022': '/series/indian-premier-league-2022-1298423/match-schedule-fixtures-and-results',
 '2021': '/series/ipl-2021-1249214/match-schedule-fixtures-and-results',
 '2020/21': '/series/ipl-2020-21-1210595/match-schedule-fixtures-and-results',
 '2019': '/series/ipl-2019-1165643/match-schedule-fixtures-and-results',
 '2018': '/series/ipl-2018-1131611/match-schedule-fixtures-and-results',
 '2017': '/series/ipl-2017-1078425/match-schedule-fixtures-and-results',
 '2016': '/series/ipl-2016-968923/match-schedule-fixtures-and-results',
 '2015': '/series/pepsi-indian-premier-league-2015-791129/match-schedule-fixtures-and-results',
 '2014': '/series/pepsi-indian-premier-league-2014-695871/match-schedule-fixtures-and-results',
 '2013': '/series/indian-premier-league-2013-586733/match-schedule-fixtures-and-results',
 '2012': '/series/indian-premier-league-2012-520932/match-schedule-fixtures-and-results',
 '2011': '/series/indian-premier-league-2011-466304/match-schedule-fixtures-and-results',
 '20

In [453]:
all_seasons = {'2023': '/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results',
 '2022': '/series/indian-premier-league-2022-1298423/match-schedule-fixtures-and-results',
 '2021': '/series/ipl-2021-1249214/match-schedule-fixtures-and-results',
 '2020/21': '/series/ipl-2020-21-1210595/match-schedule-fixtures-and-results',
 '2019': '/series/ipl-2019-1165643/match-schedule-fixtures-and-results',
 '2018': '/series/ipl-2018-1131611/match-schedule-fixtures-and-results',
 '2017': '/series/ipl-2017-1078425/match-schedule-fixtures-and-results',
 '2016': '/series/ipl-2016-968923/match-schedule-fixtures-and-results',
 '2015': '/series/pepsi-indian-premier-league-2015-791129/match-schedule-fixtures-and-results',
 '2014': '/series/pepsi-indian-premier-league-2014-695871/match-schedule-fixtures-and-results',
 '2013': '/series/indian-premier-league-2013-586733/match-schedule-fixtures-and-results',
 '2012': '/series/indian-premier-league-2012-520932/match-schedule-fixtures-and-results',
 '2011': '/series/indian-premier-league-2011-466304/match-schedule-fixtures-and-results',
 '2009/10': '/series/indian-premier-league-2009-10-418064/match-schedule-fixtures-and-results',
 '2009': '/series/indian-premier-league-2009-374163/match-schedule-fixtures-and-results',
 '2007/08': '/series/indian-premier-league-2007-08-313494/match-schedule-fixtures-and-results'}

In [486]:
if(len(json_obj['team1_overs'].split('.'))==2):
    extra_one = 1
else:
    extra_one = 0

In [489]:
master_summary = {}
spl_matches = []
for year, series_link in all_seasons.items():
    print(year)
    data = []

    espncricinfo = 'https://www.espncricinfo.com'
    url = espncricinfo + series_link
    print(url)
    driver.get(url)

    html = driver.page_source.encode('utf-8')
    page_num = 0
    content = driver.page_source
    page_soup = soup(driver.page_source, 'lxml')

    containers = page_soup.findAll(
    "div", {"class": "ds-p-4"})

    for item in containers:
        json_obj = {}
        try:
            if(item.find('div', attrs={'class': 'ds-text-compact-xs ds-font-bold ds-w-24'})):
                json_obj['date'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[2] + item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[3]
            json_obj['id'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('/match-report', '').split('-')[-1]
            json_obj['description'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text
            if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 0):
                json_obj['team1'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[0].text
            if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 1):
                json_obj['team2'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[1].text
            if(len(item.findAll('strong', attrs={'class': ''})) > 0):
                json_obj['team1_score'] = item.findAll('strong', attrs={'class': ''})[0].text
                json_obj['team1_runs'] = json_obj['team1_score'].split('/')[0]
                if(len(json_obj['team1_score'].split('/'))==1):
                    json_obj['team1_wickets'] = '10'
                else:
                    json_obj['team1_wickets'] = json_obj['team1_score'].split('/')[1]
            if(len(item.findAll('strong', attrs={'class': ''})) > 1):
                json_obj['team2_score'] = item.findAll('strong', attrs={'class': ''})[1].text
                json_obj['team2_runs'] = json_obj['team2_score'].split('/')[0]
                if(len(json_obj['team2_score'].split('/'))==1):
                    json_obj['team2_wickets'] = '10'
                else:
                    json_obj['team2_wickets'] = json_obj['team2_score'].split('/')[1]
            json_obj['result'] = item.find('p', attrs={'class': 'ds-text-tight-s ds-font-regular ds-line-clamp-2 ds-text-typo'})['title']
            json_obj['live_score_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','live-cricket-score')
            json_obj['match_overs_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','match-overs-comparison')
            data.append(json_obj)
        except:
            # print(e)
            pass

    match_pd = pd.DataFrame.from_dict(data)
    print(year, ": ", len(match_pd))

    data = []
    for index, row in match_pd.iterrows():
        url = espncricinfo + row['live_score_link']
        id = row['id']
        team1 = row['team1']
        team2 = row['team2']
        driver.get(url)
        print("Fetched Page", id, "-", team1, team2)
        page_num = 0
        content = driver.page_source
        page_soup = soup(driver.page_source, 'lxml')

        json_obj = {}
        try:
            table = page_soup.find("table", {"class": "ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"})
            match_details = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
        
            json_obj['id'] = id
            json_obj['venue_name'] = match_details[0].text
            json_obj['city'] = match_details[0].text.split(',')[-1]
            json_obj['venue_id'] = table.find("a", {"class": "ds-inline-flex ds-items-start ds-leading-none"})['href'].replace(".html", "").split("/")[-1]
            json_obj['toss_won'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[0]
            if('field' in table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[1]):
                json_obj['decision'] = 'BOWL FIRST'
            else:
                json_obj['decision'] = 'BAT FIRST'
            json_obj['pom'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block ds-ml-2"})[0].text
            json_obj['points'] = table.findAll("span", {"class":"ds-text-tight-s ds-font-regular"})[2].text
            json_obj['super_over'] = "FALSE"
            if(len(page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"}))>=1):
                json_obj['team1_overs'] = page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"})[0].text.replace("(", "").split(' ')[0]
            else:
                json_obj['team1_overs'] = 0
            if(len(page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"}))>=2):
                json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"})[1].text.replace("(", "").split(' ')[0]
            else:
                json_obj['team2_overs'] = 0
            print('team2 overs: ', json_obj['team2_overs'], 'team1 overs: ', json_obj['team1_overs'])
            if(team1 in json_obj['points'].split(',')[0]):
                json_obj['winner'] = team1
            else:
                json_obj['winner'] = team2
            if('1' in json_obj['points']):
                json_obj['winner'] = 'No Result'

            key_players = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
            json_obj['team1_key_batters'] = key_players[0].text + ', ' + key_players[2].text
            json_obj['team1_key_bowlers'] = key_players[5].text + ', ' + key_players[7].text
            json_obj['team2_key_batters'] = key_players[4].text + ', ' + key_players[6].text
            json_obj['team2_key_bowlers'] = key_players[1].text + ', ' + key_players[3].text
            data.append(json_obj)
            print("Match", len(data), "Toss and Details Done")
        except Exception as e:
            pass
            # raise e

    match_2_pd = pd.DataFrame.from_dict(data)
    overall_summary = match_2_pd.join(match_pd.set_index('id'), on='id')
    overall_summary_copy = overall_summary.copy()
    data = []

    for index, row in overall_summary_copy.iterrows():
        try:
            url = espncricinfo + row['match_overs_link']
            id = row['id']
            if(len(row['team1_overs'].split('.'))==2):
                extra_one = 1
            else:
                extra_one = 0
            
            if(len(row['team2_overs'].split('.'))==2):
                extra_two = 1
            else:
                extra_two = 0
            
            try:
                team1_overs = min(int(float(row['team1_overs'])) + extra_one, 20)
            except:
                team1_overs = 0
            try:
                team2_overs = min(int(float(row['team2_overs'])) + extra_two, 20)
            except: 
                team2_overs = 0
            driver.get(url)
            # print("Fetched Page", id)
            page_num = 0
            content = driver.page_source
            page_soup = soup(driver.page_source, 'lxml')

            over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

            all_over_count = 1
            team1_ocount = 1
            team2_ocount = 1
            team1_runs = []
            team1_wickets = []
            team2_runs = []
            team2_wickets = []

            json_obj = {}
            json_obj['id'] = id
            for over in over_details:
                over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
                if ((all_over_count%2==0) and (team2_ocount <= team2_overs)):
                    team2_runs.append(over_desc.split(" ")[0])
                    team2_wickets.append(over_desc.split(" ")[2])
                    team2_ocount += 1
                elif (team1_ocount <= team1_overs):
                    team1_runs.append(over_desc.split(" ")[0])
                    team1_wickets.append(over_desc.split(" ")[2])
                    team1_ocount += 1
                all_over_count += 1

            # team1_runs = [eval(i) for i in team1_runs]
            # team2_runs = [eval(i) for i in team2_runs]
            # team1_wickets = [eval(i) for i in team1_wickets]
            # team2_wickets = [eval(i) for i in team2_wickets]

            print('Actual Overs', row['team1_overs'], row['team2_overs'])
            print('team1_overs',team1_overs, 'team2_overs', team2_overs)
            print('team1_runs',team1_runs)
            print('team2_runs',team2_runs)
            print('team1_wickets',team1_wickets)
            print('team2_wickets',team2_wickets)
            team1_pp_runs_scored = team1_middle_runs_scored = team1_death_runs_scored = 0
            team1_pp_wickets_lost = team1_middle_wickets_lost = team1_death_wickets_lost = 0

            team2_pp_runs_scored = team2_middle_runs_scored = team2_death_runs_scored = 0
            team2_pp_wickets_lost = team2_middle_wickets_lost = team2_death_wickets_lost = 0

            team1_ocount = 1
            team2_ocount = 1
            
            for i in range(20):
                if i<6:
                    if (team1_ocount <= team1_overs):
                        team1_pp_runs_scored += int(team1_runs[i])
                        team1_pp_wickets_lost += int(team1_wickets[i])
                        team1_ocount += 1
                    if (team2_ocount <= team2_overs):
                        team2_pp_runs_scored += int(team2_runs[i])
                        team2_pp_wickets_lost += int(team2_wickets[i])
                        team2_ocount += 1
                elif (6<=i<=14):
                    if (team1_ocount <= team1_overs):
                        team1_middle_runs_scored += int(team1_runs[i])
                        team1_middle_wickets_lost += int(team1_wickets[i])
                        team1_ocount += 1
                    if (team2_ocount <= team2_overs):
                        team2_middle_runs_scored += int(team2_runs[i])
                        team2_middle_wickets_lost += int(team2_wickets[i])
                        team2_ocount += 1
                elif i>14:
                    if (team1_ocount <= team1_overs):
                        team1_death_runs_scored += int(team1_runs[i])
                        team1_death_wickets_lost += int(team1_wickets[i])
                        team1_ocount += 1
                    if (team2_ocount <= team2_overs):
                        team2_death_runs_scored += int(team2_runs[i])
                        team2_death_wickets_lost += int(team2_wickets[i])
                        team2_ocount += 1

            json_obj['team1_pp_runs_scored'] = team1_pp_runs_scored 
            json_obj['team1_middle_runs_scored'] = team1_middle_runs_scored
            json_obj['team1_death_runs_scored'] = team1_death_runs_scored

            if(team1_overs>0):
                json_obj['team1_pp_run_rate'] = team1_pp_runs_scored/min(team1_overs, 6)
            else:
                json_obj['team1_pp_run_rate']
            if(team1_overs>6):
                json_obj['team1_middle_run_rate'] = team1_middle_runs_scored/min(team1_overs-6, 9)
            else:
                json_obj['team1_middle_run_rate'] = 0
            if(team2_overs>15):
                json_obj['team1_death_run_rate'] = team1_death_runs_scored/min(team1_overs-15, 5)
            else:
                json_obj['team1_death_run_rate'] = 0

            json_obj['team1_pp_wickets_lost'] = team1_pp_wickets_lost
            json_obj['team1_middle_wickets_lost'] = team1_middle_wickets_lost
            json_obj['team1_death_wickets_lost'] = team1_death_wickets_lost

            json_obj['team2_pp_runs_scored'] = team2_pp_runs_scored
            json_obj['team2_middle_runs_scored'] = team2_middle_runs_scored
            json_obj['team2_death_runs_scored'] = team2_death_runs_scored

            if(team2_overs>0):
                json_obj['team2_pp_run_rate'] = team2_pp_runs_scored/min(team2_overs, 6)
            else:
                json_obj['team2_pp_run_rate']
            if(team2_overs>6):
                json_obj['team2_middle_run_rate'] = team2_middle_runs_scored/min(team2_overs-6, 9)
            else:
                json_obj['team2_middle_run_rate'] = 0
            if(team2_overs>15):
                json_obj['team2_death_run_rate'] = team2_death_runs_scored/min(team2_overs-15, 5)
            else:
                json_obj['team2_death_run_rate'] = 0

            json_obj['team2_pp_wickets_lost'] = team2_pp_wickets_lost
            json_obj['team2_middle_wickets_lost'] = team2_middle_wickets_lost
            json_obj['team2_death_wickets_lost'] = team2_death_wickets_lost

            data.append(json_obj)
            print("Match", len(data), "Over-wise done")
            print(json_obj)
        except Exception as e:
            spl_match = {}
            spl_match['id'] = id
            spl_match['url'] = url
            spl_match['error'] = e
            spl_matches.append(spl_match)
            pass
        
    match_3_pd = pd.DataFrame.from_dict(data)
    overall_summary = overall_summary.join(match_3_pd.set_index('id'), on='id')
    master_summary[year] = overall_summary

2023
https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results
2023 :  74
Fetched Page 1359475 - CSK GT
team2 overs:  19.2 team1 overs:  20
Match 1 Toss and Details Done
Fetched Page 1359476 - PBKS KKR
team2 overs:  16 team1 overs:  20
Match 2 Toss and Details Done
Fetched Page 1359477 - LSG DC
team2 overs:  20 team1 overs:  20
Match 3 Toss and Details Done
Fetched Page 1359478 - RR SRH
team2 overs:  20 team1 overs:  20
Match 4 Toss and Details Done
Fetched Page 1359479 - MI RCB
team2 overs:  16.2 team1 overs:  20
Match 5 Toss and Details Done
Fetched Page 1359480 - CSK LSG
team2 overs:  20 team1 overs:  20
Match 6 Toss and Details Done
Fetched Page 1359481 - DC GT
team2 overs:  18.1 team1 overs:  20
Match 7 Toss and Details Done
Fetched Page 1359482 - PBKS RR
team2 overs:  20 team1 overs:  20
Match 8 Toss and Details Done
Fetched Page 1359483 - KKR RCB
team2 overs:  17.4 team1 overs:  20
Match 9 Toss and Details Done
Fetched Page 135948

### 2023 Season

In [6]:
season_2023 = {'2023': '/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results'}

master_summary = {}
spl_matches = []
for year, series_link in season_2023.items():
    print(year)
    data = []

    espncricinfo = 'https://www.espncricinfo.com'
    url = espncricinfo + series_link
    print(url)
    driver.get(url)

    html = driver.page_source.encode('utf-8')
    page_num = 0
    content = driver.page_source
    page_soup = soup(driver.page_source, 'lxml')

    containers = page_soup.findAll(
    "div", {"class": "ds-p-4"})

    for item in containers:
        json_obj = {}
        try:
            if(item.find('div', attrs={'class': 'ds-text-compact-xs ds-font-bold ds-w-24'})):
                json_obj['date'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[2] + item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[3]
            json_obj['id'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('/match-report', '').split('-')[-1]
            json_obj['description'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text
            if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 0):
                json_obj['team1'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[0].text
            if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 1):
                json_obj['team2'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[1].text
            if(len(item.findAll('strong', attrs={'class': ''})) > 0):
                json_obj['team1_score'] = item.findAll('strong', attrs={'class': ''})[0].text
                json_obj['team1_runs'] = json_obj['team1_score'].split('/')[0]
                if(len(json_obj['team1_score'].split('/'))==1):
                    json_obj['team1_wickets'] = '10'
                else:
                    json_obj['team1_wickets'] = json_obj['team1_score'].split('/')[1]
            if(len(item.findAll('strong', attrs={'class': ''})) > 1):
                json_obj['team2_score'] = item.findAll('strong', attrs={'class': ''})[1].text
                json_obj['team2_runs'] = json_obj['team2_score'].split('/')[0]
                if(len(json_obj['team2_score'].split('/'))==1):
                    json_obj['team2_wickets'] = '10'
                else:
                    json_obj['team2_wickets'] = json_obj['team2_score'].split('/')[1]
            json_obj['result'] = item.find('p', attrs={'class': 'ds-text-tight-s ds-font-regular ds-line-clamp-2 ds-text-typo'})['title']
            json_obj['live_score_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','live-cricket-score')
            json_obj['match_overs_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','match-overs-comparison')
            data.append(json_obj)
        except:
            # print(e)
            pass

    match_pd = pd.DataFrame.from_dict(data)
    print(year, ": ", len(match_pd))

    data = []
    for index, row in match_pd.iterrows():
        url = espncricinfo + row['live_score_link']
        id = row['id']
        team1 = row['team1']
        team2 = row['team2']
        driver.get(url)
        print("Fetched Page", id, "-", team1, team2)
        page_num = 0
        content = driver.page_source
        page_soup = soup(driver.page_source, 'lxml')

        json_obj = {}
        try:
            table = page_soup.find("table", {"class": "ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"})
            match_details = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
        
            json_obj['id'] = id
            json_obj['venue_name'] = match_details[0].text
            json_obj['city'] = match_details[0].text.split(',')[-1]
            json_obj['venue_id'] = table.find("a", {"class": "ds-inline-flex ds-items-start ds-leading-none"})['href'].replace(".html", "").split("/")[-1]
            json_obj['toss_won'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[0]
            if('field' in table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[1]):
                json_obj['decision'] = 'BOWL FIRST'
            else:
                json_obj['decision'] = 'BAT FIRST'
            json_obj['pom'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block ds-ml-2"})[0].text
            json_obj['points'] = table.findAll("span", {"class":"ds-text-tight-s ds-font-regular"})[2].text
            json_obj['super_over'] = "FALSE"
            if(len(page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"}))>=1):
                json_obj['team1_overs'] = page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"})[0].text.replace("(", "").split(' ')[0]
            else:
                json_obj['team1_overs'] = 0
            if(len(page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"}))>=2):
                json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-ml-1 ds-capitalize"})[1].text.replace("(", "").split(' ')[0]
            else:
                json_obj['team2_overs'] = 0
            print('team2 overs: ', json_obj['team2_overs'], 'team1 overs: ', json_obj['team1_overs'])
            if(team1 in json_obj['points'].split(',')[0]):
                json_obj['winner'] = team1
            else:
                json_obj['winner'] = team2
            if('1' in json_obj['points']):
                json_obj['winner'] = 'No Result'

            key_players = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
            json_obj['team1_key_batters'] = key_players[0].text + ', ' + key_players[2].text
            json_obj['team1_key_bowlers'] = key_players[5].text + ', ' + key_players[7].text
            json_obj['team2_key_batters'] = key_players[4].text + ', ' + key_players[6].text
            json_obj['team2_key_bowlers'] = key_players[1].text + ', ' + key_players[3].text
            data.append(json_obj)
            print("Match", len(data), "Toss and Details Done")
        except Exception as e:
            pass
            # raise e

    match_2_pd = pd.DataFrame.from_dict(data)
    overall_summary = match_2_pd.join(match_pd.set_index('id'), on='id')
    overall_summary_copy = overall_summary.copy()
    data = []

    for index, row in overall_summary_copy.iterrows():
        try:
            url = espncricinfo + row['match_overs_link']
            id = row['id']
            if(len(row['team1_overs'].split('.'))==2):
                extra_one = 1
            else:
                extra_one = 0
            
            if(len(row['team2_overs'].split('.'))==2):
                extra_two = 1
            else:
                extra_two = 0
            
            try:
                team1_overs = min(int(float(row['team1_overs'])) + extra_one, 20)
            except:
                team1_overs = 0
            try:
                team2_overs = min(int(float(row['team2_overs'])) + extra_two, 20)
            except: 
                team2_overs = 0
            driver.get(url)
            # print("Fetched Page", id)
            page_num = 0
            content = driver.page_source
            page_soup = soup(driver.page_source, 'lxml')

            over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

            all_over_count = 1
            team1_ocount = 1
            team2_ocount = 1
            team1_runs = []
            team1_wickets = []
            team2_runs = []
            team2_wickets = []

            json_obj = {}
            json_obj['id'] = id
            for over in over_details:
                over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
                if ((all_over_count%2==0) and (team2_ocount <= team2_overs)):
                    team2_runs.append(over_desc.split(" ")[0])
                    team2_wickets.append(over_desc.split(" ")[2])
                    team2_ocount += 1
                elif (team1_ocount <= team1_overs):
                    team1_runs.append(over_desc.split(" ")[0])
                    team1_wickets.append(over_desc.split(" ")[2])
                    team1_ocount += 1
                all_over_count += 1

            # team1_runs = [eval(i) for i in team1_runs]
            # team2_runs = [eval(i) for i in team2_runs]
            # team1_wickets = [eval(i) for i in team1_wickets]
            # team2_wickets = [eval(i) for i in team2_wickets]

            print('Actual Overs', row['team1_overs'], row['team2_overs'])
            print('team1_overs',team1_overs, 'team2_overs', team2_overs)
            print('team1_runs',team1_runs)
            print('team2_runs',team2_runs)
            print('team1_wickets',team1_wickets)
            print('team2_wickets',team2_wickets)
            team1_pp_runs_scored = team1_middle_runs_scored = team1_death_runs_scored = 0
            team1_pp_wickets_lost = team1_middle_wickets_lost = team1_death_wickets_lost = 0

            team2_pp_runs_scored = team2_middle_runs_scored = team2_death_runs_scored = 0
            team2_pp_wickets_lost = team2_middle_wickets_lost = team2_death_wickets_lost = 0

            team1_ocount = 1
            team2_ocount = 1
            
            for i in range(20):
                if i<6:
                    if (team1_ocount <= team1_overs):
                        team1_pp_runs_scored += int(team1_runs[i])
                        team1_pp_wickets_lost += int(team1_wickets[i])
                        team1_ocount += 1
                    if (team2_ocount <= team2_overs):
                        team2_pp_runs_scored += int(team2_runs[i])
                        team2_pp_wickets_lost += int(team2_wickets[i])
                        team2_ocount += 1
                elif (6<=i<=14):
                    if (team1_ocount <= team1_overs):
                        team1_middle_runs_scored += int(team1_runs[i])
                        team1_middle_wickets_lost += int(team1_wickets[i])
                        team1_ocount += 1
                    if (team2_ocount <= team2_overs):
                        team2_middle_runs_scored += int(team2_runs[i])
                        team2_middle_wickets_lost += int(team2_wickets[i])
                        team2_ocount += 1
                elif i>14:
                    if (team1_ocount <= team1_overs):
                        team1_death_runs_scored += int(team1_runs[i])
                        team1_death_wickets_lost += int(team1_wickets[i])
                        team1_ocount += 1
                    if (team2_ocount <= team2_overs):
                        team2_death_runs_scored += int(team2_runs[i])
                        team2_death_wickets_lost += int(team2_wickets[i])
                        team2_ocount += 1

            json_obj['team1_pp_runs_scored'] = team1_pp_runs_scored 
            json_obj['team1_middle_runs_scored'] = team1_middle_runs_scored
            json_obj['team1_death_runs_scored'] = team1_death_runs_scored

            if(team1_overs>0):
                json_obj['team1_pp_run_rate'] = team1_pp_runs_scored/min(team1_overs, 6)
            else:
                json_obj['team1_pp_run_rate']
            if(team1_overs>6):
                json_obj['team1_middle_run_rate'] = team1_middle_runs_scored/min(team1_overs-6, 9)
            else:
                json_obj['team1_middle_run_rate'] = 0
            if(team2_overs>15):
                json_obj['team1_death_run_rate'] = team1_death_runs_scored/min(team1_overs-15, 5)
            else:
                json_obj['team1_death_run_rate'] = 0

            json_obj['team1_pp_wickets_lost'] = team1_pp_wickets_lost
            json_obj['team1_middle_wickets_lost'] = team1_middle_wickets_lost
            json_obj['team1_death_wickets_lost'] = team1_death_wickets_lost

            json_obj['team2_pp_runs_scored'] = team2_pp_runs_scored
            json_obj['team2_middle_runs_scored'] = team2_middle_runs_scored
            json_obj['team2_death_runs_scored'] = team2_death_runs_scored

            if(team2_overs>0):
                json_obj['team2_pp_run_rate'] = team2_pp_runs_scored/min(team2_overs, 6)
            else:
                json_obj['team2_pp_run_rate']
            if(team2_overs>6):
                json_obj['team2_middle_run_rate'] = team2_middle_runs_scored/min(team2_overs-6, 9)
            else:
                json_obj['team2_middle_run_rate'] = 0
            if(team2_overs>15):
                json_obj['team2_death_run_rate'] = team2_death_runs_scored/min(team2_overs-15, 5)
            else:
                json_obj['team2_death_run_rate'] = 0

            json_obj['team2_pp_wickets_lost'] = team2_pp_wickets_lost
            json_obj['team2_middle_wickets_lost'] = team2_middle_wickets_lost
            json_obj['team2_death_wickets_lost'] = team2_death_wickets_lost

            data.append(json_obj)
            print("Match", len(data), "Over-wise done")
            print(json_obj)
        except Exception as e:
            spl_match = {}
            spl_match['id'] = id
            spl_match['url'] = url
            spl_match['error'] = e
            spl_matches.append(spl_match)
            pass
        
    match_3_pd = pd.DataFrame.from_dict(data)
    overall_summary = overall_summary.join(match_3_pd.set_index('id'), on='id')
    master_summary[year] = overall_summary

2023
https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results
2023 :  74
Fetched Page 1359475 - CSK GT
team2 overs:  19.2 team1 overs:  20
Match 1 Toss and Details Done
Fetched Page 1359476 - PBKS KKR
team2 overs:  16 team1 overs:  20
Match 2 Toss and Details Done
Fetched Page 1359477 - LSG DC
team2 overs:  20 team1 overs:  20
Match 3 Toss and Details Done
Fetched Page 1359478 - RR SRH
team2 overs:  20 team1 overs:  20
Match 4 Toss and Details Done
Fetched Page 1359479 - MI RCB
team2 overs:  16.2 team1 overs:  20
Match 5 Toss and Details Done
Fetched Page 1359480 - CSK LSG
team2 overs:  20 team1 overs:  20
Match 6 Toss and Details Done
Fetched Page 1359481 - DC GT
team2 overs:  18.1 team1 overs:  20
Match 7 Toss and Details Done
Fetched Page 1359482 - PBKS RR
team2 overs:  20 team1 overs:  20
Match 8 Toss and Details Done
Fetched Page 1359483 - KKR RCB
team2 overs:  17.4 team1 overs:  20
Match 9 Toss and Details Done
Fetched Page 135948

In [5]:
master_summary.keys()

dict_keys(['2023'])

In [623]:
for key, data in master_summary.items():
    if key=='2023':
        continue
    elif key=='2022':
        print(key)
        ipl_2022 = data.copy()
    else:
        print(key)
        ipl_2022 = pd.concat([ipl_2022, data])

2022
2021
2020/21
2019
2018
2017
2016
2015
2014
2013
2012
2011
2009/10
2009
2007/08


In [6]:
for key, data in master_summary.items():
    print(key)
    if key=='2023':
        ipl_all_seasons = data.copy()
    else:
        ipl_all_seasons = pd.concat([ipl_all_seasons, data])

2023


In [18]:
len(ipl_all_seasons)

67

In [7]:
ipl_all_seasons.to_csv('ipl_all_seasons_dump_v4.csv', index=False)

# Fixing Special Matches

In [490]:
spl_matches

[{'id': '1359511',
  'url': 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/rajasthan-royals-vs-chennai-super-kings-37th-match-1359511/match-overs-comparison',
  'error': selenium.common.exceptions.TimeoutException()},
 {'id': '1359512',
  'url': 'https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/punjab-kings-vs-lucknow-super-giants-38th-match-1359512/match-overs-comparison',
  'error': selenium.common.exceptions.TimeoutException()},
 {'id': '1304052',
  'url': 'https://www.espncricinfo.com/series/indian-premier-league-2022-1298423/royal-challengers-bangalore-vs-kolkata-knight-riders-6th-match-1304052/match-overs-comparison',
  'error': IndexError('list index out of range')},
 {'id': '598014',
  'url': 'https://www.espncricinfo.com/series/indian-premier-league-2013-586733/rajasthan-royals-vs-kings-xi-punjab-18th-match-598014/match-overs-comparison',
  'error': IndexError('list index out of range')},
 {'id': '501218',
  'url': 'https://www.es

In [47]:
url = 'https://www.espncricinfo.com/series/indian-premier-league-2022-1298423/royal-challengers-bangalore-vs-sunrisers-hyderabad-36th-match-1304082/match-overs-comparison'
driver.get(url)

In [48]:
html = driver.page_source.encode('utf-8')
page_num = 0
content = driver.page_source
page_soup = soup(driver.page_source, 'lxml')

In [56]:
data = []
for year, series_link in all_seasons.items():
    print(year)

    espncricinfo = 'https://www.espncricinfo.com'
    url = espncricinfo + series_link
    print(url)
    driver.get(url)

    html = driver.page_source.encode('utf-8')
    page_num = 0
    content = driver.page_source
    page_soup = soup(driver.page_source, 'lxml')

    containers = page_soup.findAll(
    "div", {"class": "ds-p-4"})

    for item in containers:
        json_obj = {}
        try:
            if(item.find('div', attrs={'class': 'ds-text-compact-xs ds-font-bold ds-w-24'})):
                json_obj['date'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[2] + item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text.split(',')[3]
            json_obj['id'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('/match-report', '').split('-')[-1]
            json_obj['description'] = item.find('div', attrs={'class': 'ds-text-tight-xs ds-truncate ds-text-typo-mid3'}).text
            if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 0):
                json_obj['team1'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[0].text
            if(len(item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})) > 1):
                json_obj['team2'] = item.findAll('p', attrs={'class': 'ds-text-tight-m ds-font-bold ds-capitalize ds-truncate'})[1].text
            if(len(item.findAll('strong', attrs={'class': ''})) > 0):
                json_obj['team1_score'] = item.findAll('strong', attrs={'class': ''})[0].text
                json_obj['team1_runs'] = json_obj['team1_score'].split('/')[0]
                if(len(json_obj['team1_score'].split('/'))==1):
                    json_obj['team1_wickets'] = '10'
                else:
                    json_obj['team1_wickets'] = json_obj['team1_score'].split('/')[1]
            if(len(item.findAll('strong', attrs={'class': ''})) > 1):
                json_obj['team2_score'] = item.findAll('strong', attrs={'class': ''})[1].text
                json_obj['team2_runs'] = json_obj['team2_score'].split('/')[0]
                if(len(json_obj['team2_score'].split('/'))==1):
                    json_obj['team2_wickets'] = '10'
                else:
                    json_obj['team2_wickets'] = json_obj['team2_score'].split('/')[1]
            json_obj['result'] = item.find('p', attrs={'class': 'ds-text-tight-s ds-font-regular ds-line-clamp-2 ds-text-typo'})['title']
            json_obj['live_score_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','live-cricket-score')
            json_obj['match_overs_link'] = item.find('a', attrs={'class': 'ds-inline-flex ds-items-start ds-leading-none'})['href'].replace('match-report','match-overs-comparison')
            # json_obj['live_score'] = json_obj['live_score'].str.replace('match-report','live-cricket-score')
            data.append(json_obj)
        except:
            # print(e)
            pass
        
match_pd = pd.DataFrame.from_dict(data)
spl_matches_pd = pd.DataFrame.from_dict(spl_matches)
match_pd = spl_matches_pd.join(match_pd.set_index('id'), on='id')

2023
https://www.espncricinfo.com/series/indian-premier-league-2023-1345038/match-schedule-fixtures-and-results
2022
https://www.espncricinfo.com/series/indian-premier-league-2022-1298423/match-schedule-fixtures-and-results
2021
https://www.espncricinfo.com/series/ipl-2021-1249214/match-schedule-fixtures-and-results
2020/21
https://www.espncricinfo.com/series/ipl-2020-21-1210595/match-schedule-fixtures-and-results
2019
https://www.espncricinfo.com/series/ipl-2019-1165643/match-schedule-fixtures-and-results
2018
https://www.espncricinfo.com/series/ipl-2018-1131611/match-schedule-fixtures-and-results
2017
https://www.espncricinfo.com/series/ipl-2017-1078425/match-schedule-fixtures-and-results
2016
https://www.espncricinfo.com/series/ipl-2016-968923/match-schedule-fixtures-and-results
2015
https://www.espncricinfo.com/series/pepsi-indian-premier-league-2015-791129/match-schedule-fixtures-and-results
2014
https://www.espncricinfo.com/series/pepsi-indian-premier-league-2014-695871/match-sch

In [57]:
super_spl_matches = []
data = []

for index, row in match_pd.iterrows():
    url = espncricinfo + row['live_score_link']
    id = row['id']
    team1 = row['team1']
    team2 = row['team2']
    driver.get(url)
    print("Fetched Page", id, "-", team1, team2)
    page_num = 0
    content = driver.page_source
    page_soup = soup(driver.page_source, 'lxml')

    json_obj = {}
    try:
        table = page_soup.find("table", {"class": "ds-w-full ds-table ds-table-sm ds-table-auto lg:ds-border-b ds-border-line"})
        match_details = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
    
        json_obj['id'] = id
        json_obj['venue_name'] = match_details[0].text
        json_obj['city'] = match_details[0].text.split(',')[-1]
        json_obj['venue_id'] = table.find("a", {"class": "ds-inline-flex ds-items-start ds-leading-none"})['href'].replace(".html", "").split("/")[-1]
        json_obj['toss_won'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[0]
        if('field' in table.findAll("span", {"class": "ds-text-tight-s ds-font-regular"})[0].text.split(',')[1]):
            json_obj['decision'] = 'BOWL FIRST'
        else:
            json_obj['decision'] = 'BAT FIRST'
        json_obj['pom'] = table.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block ds-ml-2"})[0].text
        json_obj['points'] = table.findAll("span", {"class":"ds-text-tight-s ds-font-regular"})[2].text
        json_obj['super_over'] = "FALSE"
        json_obj['team2_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[1].text.split(',')[0].replace("/20 ov", "").replace("(", "").replace(" ov", "").split('/')[0]
        # json_obj['team2_overs'] = json_obj['team2_overs'].replace("(", "").replace(" ov", "").split('/')[0]
        if (page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[0].text==''):
            json_obj['team1_overs'] = "20"
        else:
            json_obj['team1_overs'] = page_soup.findAll("span", {"class": "ds-text-compact-s ds-mr-0.5"})[0].text.split(',')[0].replace("/20 ov", "").replace("(", "").replace(" ov", "").split('/')[0]

        # print('team2 overs: ', json_obj['team2_overs'], 'team1 overs: ', json_obj['team1_overs'])
        if(team1 in json_obj['points'].split(',')[0]):
            json_obj['winner'] = team1
        else:
            json_obj['winner'] = team2
        if('1' in json_obj['points']):
            json_obj['winner'] = 'No Result'

        key_players = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-medium ds-text-typo ds-underline ds-decoration-ui-stroke hover:ds-text-typo-primary hover:ds-decoration-ui-stroke-primary ds-block"})
        json_obj['team1_key_batters'] = key_players[0].text + ', ' + key_players[2].text
        json_obj['team1_key_bowlers'] = key_players[5].text + ', ' + key_players[7].text
        json_obj['team2_key_batters'] = key_players[4].text + ', ' + key_players[6].text
        json_obj['team2_key_bowlers'] = key_players[1].text + ', ' + key_players[3].text
        print("Match", len(data) + 1, "Toss and Details Done")
    except Exception as e:
        pass
        # raise e

    try:
        url = espncricinfo + row['match_overs_link']
        id = row['id']
        driver.get(url)
        # print("Fetched Page", id)
        page_num = 0
        content = driver.page_source
        page_soup = soup(driver.page_source, 'lxml')

        over_details = page_soup.findAll("span", {"class": "ds-text-tight-s ds-font-regular ds-ml-1 ds-text-typo-mid3"})

        try:
            team1_overs = len(page_soup.findAll("div", {"class": "ds-text-tight-s ds-font-regular ds-flex ds-justify-center ds-items-center ds-w-7 ds-h-7 ds-rounded-full ds-border ds-border-ui-stroke ds-bg-fill-content-prime"}))
            json_obj['team1_overs'] = team1_overs
        except:
            team1_overs = 0
        try:
            team2_overs = int(float(json_obj['team2_overs']))
        except: 
            team2_overs = 0
        print('team2 overs: ', json_obj['team2_overs'], 'team1 overs: ', json_obj['team1_overs'])

        all_over_count = 1
        team1_ocount = 1
        team2_ocount = 1
        team1_runs = []
        team1_wickets = []
        team2_runs = []
        team2_wickets = []
        
        for over in over_details:
            over_desc = over.text.replace("<!-- -->", "").replace("(", "").replace(")", "")
            if ((all_over_count%2==0) and (team2_ocount <= team2_overs)):
                team2_runs.append(over_desc.split(" ")[0])
                team2_wickets.append(over_desc.split(" ")[2])
                team2_ocount += 1
            elif (team1_ocount <= team1_overs):
                team1_runs.append(over_desc.split(" ")[0])
                team1_wickets.append(over_desc.split(" ")[2])
                team1_ocount += 1
            all_over_count += 1

        # team1_runs = [eval(i) for i in team1_runs]
        # team2_runs = [eval(i) for i in team2_runs]
        # team1_wickets = [eval(i) for i in team1_wickets]
        # team2_wickets = [eval(i) for i in team2_wickets]

        # print(team1_runs)
        # print(team2_runs)
        team1_pp_runs_scored = team1_middle_runs_scored = team1_death_runs_scored = 0
        team1_pp_wickets_lost = team1_middle_wickets_lost = team1_death_wickets_lost = 0

        team2_pp_runs_scored = team2_middle_runs_scored = team2_death_runs_scored = 0
        team2_pp_wickets_lost = team2_middle_wickets_lost = team2_death_wickets_lost = 0

        team1_ocount = 1
        team2_ocount = 1
        
        for i in range(20):
            if i<6:
                if (team1_ocount <= team1_overs):
                    team1_pp_runs_scored += int(team1_runs[i])
                    team1_pp_wickets_lost += int(team1_wickets[i])
                    team1_ocount += 1
                if (team2_ocount <= team2_overs):
                    team2_pp_runs_scored += int(team2_runs[i])
                    team2_pp_wickets_lost += int(team2_wickets[i])
                    team2_ocount += 1
            elif (6<=i<=14):
                if (team1_ocount <= team1_overs):
                    team1_middle_runs_scored += int(team1_runs[i])
                    team1_middle_wickets_lost += int(team1_wickets[i])
                    team1_ocount += 1
                if (team2_ocount <= team2_overs):
                    team2_middle_runs_scored += int(team2_runs[i])
                    team2_middle_wickets_lost += int(team2_wickets[i])
                    team2_ocount += 1
            elif i>14:
                if (team1_ocount <= team1_overs):
                    team1_death_runs_scored += int(team1_runs[i])
                    team1_death_wickets_lost += int(team1_wickets[i])
                    team1_ocount += 1
                if (team2_ocount <= team2_overs):
                    team2_death_runs_scored += int(team2_runs[i])
                    team2_death_wickets_lost += int(team2_wickets[i])
                    team2_ocount += 1

        json_obj['team1_pp_runs_scored'] = team1_pp_runs_scored 
        json_obj['team1_middle_runs_scored'] = team1_middle_runs_scored
        json_obj['team1_death_runs_scored'] = team1_death_runs_scored

        json_obj['team1_pp_wickets_lost'] = team1_pp_wickets_lost
        json_obj['team1_middle_wickets_lost'] = team1_middle_wickets_lost
        json_obj['team1_death_wickets_lost'] = team1_death_wickets_lost

        json_obj['team2_pp_runs_scored'] = team2_pp_runs_scored
        json_obj['team2_middle_runs_scored'] = team2_middle_runs_scored
        json_obj['team2_death_runs_scored'] = team2_death_runs_scored

        json_obj['team2_pp_wickets_lost'] = team2_pp_wickets_lost
        json_obj['team2_middle_wickets_lost'] = team2_middle_wickets_lost
        json_obj['team2_death_wickets_lost'] = team2_death_wickets_lost

        data.append(json_obj)
        print("Match", len(data), "Over-wise done")
        print(json_obj)
    except Exception as e:
        super_spl_match = {}
        super_spl_match['id'] = id
        super_spl_match['url'] = url
        super_spl_match['error'] = e
        super_spl_matches.append(super_spl_match)
        pass
    
spl_matches_pd = pd.DataFrame.from_dict(data)
spl_matches_pd = match_pd.join(spl_matches_pd.set_index('id'), on='id')

Fetched Page 1304082 - RCB SRH
Match 1 Toss and Details Done
team2 overs:  8 team1 overs:  17
Match 1 Over-wise done
{'id': '1304082', 'venue_name': 'Brabourne Stadium, Mumbai', 'city': ' Mumbai', 'venue_id': '58317', 'toss_won': 'Sunrisers Hyderabad', 'decision': 'BOWL FIRST', 'pom': 'Marco Jansen', 'points': 'Sunrisers Hyderabad 2, Royal Challengers Bangalore 0', 'super_over': 'FALSE', 'team2_overs': '8', 'team1_overs': 17, 'winner': 'SRH', 'team1_key_batters': 'Suyash Prabhudessai , Glenn Maxwell ', 'team1_key_bowlers': 'Harshal Patel, Wanindu Hasaranga', 'team2_key_batters': 'Abhishek Sharma , Kane Williamson *', 'team2_key_bowlers': 'T Natarajan, Marco Jansen', 'team1_pp_runs_scored': 31, 'team1_middle_runs_scored': 34, 'team1_death_runs_scored': 3, 'team1_pp_wickets_lost': 4, 'team1_middle_wickets_lost': 4, 'team1_death_wickets_lost': 2, 'team2_pp_runs_scored': 56, 'team2_middle_runs_scored': 16, 'team2_death_runs_scored': 0, 'team2_pp_wickets_lost': 0, 'team2_middle_wickets_lost

In [58]:
spl_matches_pd = spl_matches_pd[['id', 'venue_name', 'city', 'venue_id', 'toss_won', 'decision', 'pom',
       'points', 'super_over', 'team2_overs', 'team1_overs', 'winner',
       'team1_key_batters', 'team1_key_bowlers', 'team2_key_batters',
       'team2_key_bowlers', 'date', 'description', 'team1', 'team2',
       'team1_score', 'team1_runs', 'team1_wickets', 'team2_score',
       'team2_runs', 'team2_wickets', 'result', 'live_score_link',
       'match_overs_link', 'team1_pp_runs_scored', 'team1_middle_runs_scored',
       'team1_death_runs_scored', 'team1_pp_wickets_lost',
       'team1_middle_wickets_lost', 'team1_death_wickets_lost',
       'team2_pp_runs_scored', 'team2_middle_runs_scored',
       'team2_death_runs_scored', 'team2_pp_wickets_lost',
       'team2_middle_wickets_lost', 'team2_death_wickets_lost']]

In [59]:
spl_matches_id = spl_matches_pd.id.tolist()

In [64]:
ipl_all_seasons = ipl_all_seasons[~ipl_all_seasons['id'].isin(spl_matches_id)]
ipl_all_seasons = pd.concat([ipl_all_seasons, spl_matches_pd])

In [341]:
driver.quit()

# All Season Data Analysis

In [8]:
ipl_all_seasons.columns

Index(['id', 'venue_name', 'city', 'venue_id', 'toss_won', 'decision', 'pom',
       'points', 'super_over', 'team1_overs', 'team2_overs', 'winner',
       'team1_key_batters', 'team1_key_bowlers', 'team2_key_batters',
       'team2_key_bowlers', 'date', 'description', 'team1', 'team2',
       'team1_score', 'team1_runs', 'team1_wickets', 'team2_score',
       'team2_runs', 'team2_wickets', 'result', 'live_score_link',
       'match_overs_link', 'team1_pp_runs_scored', 'team1_middle_runs_scored',
       'team1_death_runs_scored', 'team1_pp_run_rate', 'team1_middle_run_rate',
       'team1_death_run_rate', 'team1_pp_wickets_lost',
       'team1_middle_wickets_lost', 'team1_death_wickets_lost',
       'team2_pp_runs_scored', 'team2_middle_runs_scored',
       'team2_death_runs_scored', 'team2_pp_run_rate', 'team2_middle_run_rate',
       'team2_death_run_rate', 'team2_pp_wickets_lost',
       'team2_middle_wickets_lost', 'team2_death_wickets_lost'],
      dtype='object')

In [46]:
dsm = master_summary['2023'].copy()
dsm = dsm.convert_dtypes()
dsm['super_over'] = False
venue_dict = {' Ahmedabad':'GT', ' Chandigarh':'KXIP', ' Lucknow':'LSG', ' Hyderabad': 'SRH', ' Mumbai':'MI', ' Bengaluru': 'RCB', ' Chennai': 'CSK', ' Kolkata': 'KKR', ' Jaipur':'RR', ' Delhi':'DC', ' Guwahati':'RR', ' Dharamsala': 'KXIP'}
dsm['home_team'] = dsm['city']
dsm.replace({'home_team': venue_dict}, inplace=True)
dsm['season'] = 2023
dsm['winner'] = dsm.apply(lambda x: x['team1'] if int(x['team1_runs'])>int(x['team2_runs']) else x['team2'], axis=1)
dsm['away_team'] = dsm.apply(lambda x: x['team1'] if x['team2']==x['home_team'] else x['team2'], axis=1)

dsm['home_team'] = dsm['home_team'].astype('string')
dsm['team1_overs'] = dsm['team1_overs'].fillna("20")
dsm['team2_overs'] = dsm['team2_overs'].fillna("20")
dsm['team1_overs'] = dsm['team1_overs'].astype('float')
dsm['team2_overs'] = dsm['team2_overs'].astype('float')
dsm['id'] = dsm['id'].astype('float')

dsm['home_overs'] = dsm.apply(lambda x: x['team1_overs'] if x['team1']==x['home_team'] else x['team2_overs'], axis=1)
dsm['home_score'] = dsm.apply(lambda x: x['team1_runs'] if x['team1']==x['home_team'] else x['team2_runs'], axis=1)
dsm['home_wickets'] = dsm.apply(lambda x: x['team1_wickets'] if x['team1']==x['home_team'] else x['team2_wickets'], axis=1)
dsm['home_key_batter'] = dsm.apply(lambda x: x['team1_key_batters'] if x['team1']==x['home_team'] else x['team2_key_batters'], axis=1)
dsm['home_key_bowler'] = dsm.apply(lambda x: x['team1_key_bowlers'] if x['team1']==x['home_team'] else x['team2_key_bowlers'], axis=1)

dsm['away_overs'] = dsm.apply(lambda x: x['team1_overs'] if x['team1']==x['away_team'] else x['team2_overs'], axis=1)
dsm['away_score'] = dsm.apply(lambda x: x['team1_runs'] if x['team1']==x['away_team'] else x['team2_runs'], axis=1)
dsm['away_wickets'] = dsm.apply(lambda x: x['team1_wickets'] if x['team1']==x['away_team'] else x['team2_wickets'], axis=1)
dsm['away_key_batter'] = dsm.apply(lambda x: x['team1_key_batters'] if x['team1']==x['away_team'] else x['team2_key_batters'], axis=1)
dsm['away_key_bowler'] = dsm.apply(lambda x: x['team1_key_bowlers'] if x['team1']==x['away_team'] else x['team2_key_bowlers'], axis=1)

dsm['home_pp_runs_scored'] = dsm.apply(lambda x: x['team1_pp_runs_scored'] if x['team1']==x['home_team'] else x['team2_pp_runs_scored'], axis=1)
dsm['home_middle_runs_scored'] = dsm.apply(lambda x: x['team1_middle_runs_scored'] if x['team1']==x['home_team'] else x['team2_middle_runs_scored'], axis=1)
dsm['home_death_runs_scored'] = dsm.apply(lambda x: x['team1_death_runs_scored'] if x['team1']==x['home_team'] else x['team2_death_runs_scored'], axis=1)

dsm['home_pp_wickets_lost'] = dsm.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)
dsm['home_middle_wickets_lost'] = dsm.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)
dsm['home_death_wickets_lost'] = dsm.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)

dsm['away_pp_runs_scored'] = dsm.apply(lambda x: x['team1_pp_runs_scored'] if x['team1']==x['away_team'] else x['team2_pp_runs_scored'], axis=1)
dsm['away_middle_runs_scored'] = dsm.apply(lambda x: x['team1_middle_runs_scored'] if x['team1']==x['away_team'] else x['team2_middle_runs_scored'], axis=1)
dsm['away_death_runs_scored'] = dsm.apply(lambda x: x['team1_death_runs_scored'] if x['team1']==x['away_team'] else x['team2_death_runs_scored'], axis=1)

dsm['away_pp_wickets_lost'] = dsm.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)
dsm['away_middle_wickets_lost'] = dsm.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)
dsm['away_death_wickets_lost'] = dsm.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)

dsm['home_pp_run_rate'] = dsm.apply(lambda x: x['team1_pp_run_rate'] if x['team1']==x['home_team'] else x['team2_pp_run_rate'], axis=1)
dsm['home_middle_run_rate'] = dsm.apply(lambda x: x['team1_middle_run_rate'] if x['team1']==x['home_team'] else x['team2_middle_run_rate'], axis=1)
dsm['home_death_run_rate'] = dsm.apply(lambda x: x['team1_death_run_rate'] if x['team1']==x['home_team'] else x['team2_death_run_rate'], axis=1)

dsm['away_pp_run_rate'] = dsm.apply(lambda x: x['team1_pp_run_rate'] if x['team1']==x['away_team'] else x['team2_pp_run_rate'], axis=1)
dsm['away_middle_run_rate'] = dsm.apply(lambda x: x['team1_middle_run_rate'] if x['team1']==x['away_team'] else x['team2_middle_run_rate'], axis=1)
dsm['away_death_run_rate'] = dsm.apply(lambda x: x['team1_death_run_rate'] if x['team1']==x['away_team'] else x['team2_death_run_rate'], axis=1)

team_long_names = {'Gujarat Titans':'GT','Kolkata Knight Riders': 'KKR', 'Delhi Capitals':'DC', 'Sunrisers Hyderabad':'SRH', 
'Royal Challengers Bangalore':'RCB', 'Lucknow Super Giants': 'LSG', 'Rajasthan Royals':'RR', 'Chennai Super Kings':'CSK', 
'Punjab Kings':'KXIP', 'Mumbai Indians':'MI', 'Kings XI Punjab':'KXIP', 'Delhi Daredevils':'DC', 'Rising Pune Supergiants':'RPS',
'Rising Pune Supergiant':'RPS','Gujarat Lions':'GT', 'Pune Warriors':'RPS', 
'Deccan Chargers':'SRH', 'Kochi Tuskers Kerala':'Kochi'}

dsm['toss_won'] = dsm['toss_won'].fillna('CSK')
dsm['toss_won'] = dsm['toss_won'].astype('string')
dsm.replace({'toss_won': team_long_names}, inplace=True)
dsm.replace({'winner': team_long_names}, inplace=True)

dsm.replace({'winner': {'PBKS':'KXIP'}, 'toss_won':{'PBKS':'KXIP'}}, inplace=True)
dsm.replace({'winner': {'GL':'GT'}, 'toss_won':{'GL':'GT'}}, inplace=True)
dsm.replace({'winner': {'PWI':'RPS'}, 'toss_won':{'PWI':'RPS'}}, inplace=True)
# dsm.replace({'winner': {'DD':'DC'}, 'toss_won':{'DD':'DC'}}, inplace=True)

dsm.rename(columns={'team1_score':'1st_innings_score', 'team2_score':'2nd_innings_score', 'winner_new':'winner'},inplace=True)
ds_copy_cols = list(pd.read_csv('ipl_all_seasons_v6.csv').columns)

ds_copy = dsm[ds_copy_cols]

ds_copy.to_csv('ipl_2023_matches.csv', index=False)

In [41]:
osm = ipl_all_seasons.copy()
osm = osm.convert_dtypes()
osm.drop(['super_over', 'points', 'toss_won', 'winner'], axis=1, inplace=True)
# osm.rename(columns={'points':'points_2023'}, inplace=True)

In [34]:
season_summary = pd.read_csv('all_season_summary.csv')
season_summary = season_summary.convert_dtypes()
season_summary['id'] = season_summary['id'].astype('str')

In [35]:
osm = osm.join(season_summary[['home_team', 'away_team', 'season', 'super_over', 'points', 'id', 'toss_won', 'winner']].set_index('id'), on='id', how='left')

In [42]:
dsm = master_summary['2023'].copy()
dsm = dsm.convert_dtypes()
dsm['super_over'] = False
venue_dict = {' Ahmedabad':'GT', ' Chandigarh':'KXIP', ' Lucknow':'LSG', ' Hyderabad': 'SRH', ' Mumbai':'MI', ' Bengaluru': 'RCB', ' Chennai': 'CSK', ' Kolkata': 'KKR', ' Jaipur':'RR', ' Delhi':'DC', ' Guwahati':'RR', ' Dharamsala': 'KXIP'}
dsm['home_team'] = dsm['city']
dsm.replace({'home_team': venue_dict}, inplace=True)
dsm['season'] = 2023
dsm['winner'] = dsm.apply(lambda x: x['team1'] if int(x['team1_runs'])>int(x['team2_runs']) else x['team2'], axis=1)
dsm['away_team'] = dsm.apply(lambda x: x['team1'] if x['team2']==x['home_team'] else x['team2'], axis=1)

In [37]:
osum = pd.concat([osm, dsm]).sort_values(by=['season', 'id'])

In [699]:
# osum = ipl_all_seasons.copy()
# osum = osum.convert_dtypes()
# osum.drop(['super_over'], axis=1, inplace=True)
# osum.rename(columns={'points':'points_2023'}, inplace=True)

In [700]:
# osum = osum.join(season_summary[['home_team', 'away_team', 'season', 'super_over', 'points', 'id']].set_index('id'), on='id', how='left')

In [38]:
venue_dict = {' Ahmedabad':'GT', ' Chandigarh':'KXIP', ' Lucknow':'LSG', ' Hyderabad': 'SRH', ' Mumbai':'MI', ' Bengaluru': 'RCB', ' Chennai': 'CSK', ' Kolkata': 'KKR', ' Jaipur':'RR', ' Delhi':'DC', ' Guwahati':'RR', ' Dharamsala': 'KXIP'}
team_replace_dict = {'PBKS':'KXIP', 'GL':'GT', 'PWI':'RPS'}

In [702]:
# osum['points'] = osum['points'].fillna(osum['points_2023'])
# osum['points'] = osum['points'].fillna("Shared Points")

In [39]:
osum.points.head

<bound method NDFrame.head of 0             Gujarat Titans 2, Chennai Super Kings 0
1             Punjab Kings 2, Kolkata Knight Riders 0
2            Lucknow Super Giants 2, Delhi Capitals 0
3           Rajasthan Royals 2, Sunrisers Hyderabad 0
4     Royal Challengers Bangalore 2, Mumbai Indians 0
                           ...                       
62                                               <NA>
63                                               <NA>
64                                               <NA>
65                                               <NA>
66                                               <NA>
Name: points, Length: 134, dtype: string>

In [27]:
# osum['super_over'] = osum['super_over'].fillna(False)
# osum['home_team'] = osum['home_team'].fillna(osum['city'])
# osum.replace({'home_team': venue_dict}, inplace=True)

# osum['home_team'] = osum.apply(lambda x: 'SRH' if 'Deccan' in x['points'] else x['home_team'], axis=1)
# osum['away_team'] = osum.apply(lambda x: 'SRH' if 'Deccan' in x['points'] else x['away_team'], axis=1)
# osum['season'] = osum['season'].fillna(2023)
# osum = osum.convert_dtypes()
osum['home_team'] = osum['home_team'].astype('string')
osum['team1_overs'] = osum['team1_overs'].fillna("20")
osum['team2_overs'] = osum['team2_overs'].fillna("20")
osum['team1_overs'] = osum['team1_overs'].astype('float')
osum['team2_overs'] = osum['team2_overs'].astype('float')
osum['id'] = osum['id'].astype('float')

In [28]:
osum.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 134 entries, 0 to 66
Data columns (total 50 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   id                         134 non-null    float64
 1   venue_name                 134 non-null    string 
 2   city                       134 non-null    string 
 3   venue_id                   134 non-null    string 
 4   decision                   134 non-null    string 
 5   pom                        134 non-null    string 
 6   team1_overs                134 non-null    float64
 7   team2_overs                134 non-null    float64
 8   team1_key_batters          134 non-null    string 
 9   team1_key_bowlers          134 non-null    string 
 10  team2_key_batters          134 non-null    string 
 11  team2_key_bowlers          134 non-null    string 
 12  date                       134 non-null    string 
 13  description                134 non-null    string 


In [706]:
# osum['away_team'] = osum.apply(lambda x: x['team2'] if x['team1']==x['home_team'] else x['team1'], axis=1)

In [29]:
osum.replace({'home_team': {'PBKS':'KXIP'}, 'away_team':{'PBKS':'KXIP'}}, inplace=True)
osum.replace({'home_team': {'GL':'GT'}, 'away_team':{'GL':'GT'}}, inplace=True)
osum.replace({'home_team': {'PWI':'RPS'}, 'away_team':{'PWI':'RPS'}}, inplace=True)
# osum.replace({'home_team': {'DD':'DC'}, 'away_team':{'DD':'DC'}}, inplace=True)

c:\Users\Asus-2020\anaconda3\lib\site-packages\pandas\core\internals\managers.py:1911: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  op = lambda x: operator.eq(x, b)


TypeError: Cannot compare types 'ndarray(dtype=object)' and 'str'

In [708]:
osum.home_team.unique()

array(['RCB', 'KXIP', 'DC', 'MI', 'KKR', 'RR', 'SRH', 'CSK', 'Kochi',
       'RPS', 'GT', 'LSG'], dtype=object)

In [709]:
osum.away_team.unique()

array(['KKR', 'CSK', 'RR', 'RCB', 'SRH', 'KXIP', 'DC', 'MI', 'Kochi',
       'RPS', 'GT', 'LSG'], dtype=object)

In [30]:
osum['home_overs'] = osum.apply(lambda x: x['team1_overs'] if x['team1']==x['home_team'] else x['team2_overs'], axis=1)
osum['home_score'] = osum.apply(lambda x: x['team1_runs'] if x['team1']==x['home_team'] else x['team2_runs'], axis=1)
osum['home_wickets'] = osum.apply(lambda x: x['team1_wickets'] if x['team1']==x['home_team'] else x['team2_wickets'], axis=1)
osum['home_key_batter'] = osum.apply(lambda x: x['team1_key_batters'] if x['team1']==x['home_team'] else x['team2_key_batters'], axis=1)
osum['home_key_bowler'] = osum.apply(lambda x: x['team1_key_bowlers'] if x['team1']==x['home_team'] else x['team2_key_bowlers'], axis=1)

osum['away_overs'] = osum.apply(lambda x: x['team1_overs'] if x['team1']==x['away_team'] else x['team2_overs'], axis=1)
osum['away_score'] = osum.apply(lambda x: x['team1_runs'] if x['team1']==x['away_team'] else x['team2_runs'], axis=1)
osum['away_wickets'] = osum.apply(lambda x: x['team1_wickets'] if x['team1']==x['away_team'] else x['team2_wickets'], axis=1)
osum['away_key_batter'] = osum.apply(lambda x: x['team1_key_batters'] if x['team1']==x['away_team'] else x['team2_key_batters'], axis=1)
osum['away_key_bowler'] = osum.apply(lambda x: x['team1_key_bowlers'] if x['team1']==x['away_team'] else x['team2_key_bowlers'], axis=1)

TypeError: boolean value of NA is ambiguous

In [711]:
osum['home_pp_runs_scored'] = osum.apply(lambda x: x['team1_pp_runs_scored'] if x['team1']==x['home_team'] else x['team2_pp_runs_scored'], axis=1)
osum['home_middle_runs_scored'] = osum.apply(lambda x: x['team1_middle_runs_scored'] if x['team1']==x['home_team'] else x['team2_middle_runs_scored'], axis=1)
osum['home_death_runs_scored'] = osum.apply(lambda x: x['team1_death_runs_scored'] if x['team1']==x['home_team'] else x['team2_death_runs_scored'], axis=1)

osum['home_pp_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['home_middle_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['home_death_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['home_team'] else x['team2_pp_wickets_lost'], axis=1)

osum['away_pp_runs_scored'] = osum.apply(lambda x: x['team1_pp_runs_scored'] if x['team1']==x['away_team'] else x['team2_pp_runs_scored'], axis=1)
osum['away_middle_runs_scored'] = osum.apply(lambda x: x['team1_middle_runs_scored'] if x['team1']==x['away_team'] else x['team2_middle_runs_scored'], axis=1)
osum['away_death_runs_scored'] = osum.apply(lambda x: x['team1_death_runs_scored'] if x['team1']==x['away_team'] else x['team2_death_runs_scored'], axis=1)

osum['away_pp_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['away_middle_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)
osum['away_death_wickets_lost'] = osum.apply(lambda x: x['team1_pp_wickets_lost'] if x['team1']==x['away_team'] else x['team2_pp_wickets_lost'], axis=1)

osum['home_pp_run_rate'] = osum.apply(lambda x: x['team1_pp_run_rate'] if x['team1']==x['home_team'] else x['team2_pp_run_rate'], axis=1)
osum['home_middle_run_rate'] = osum.apply(lambda x: x['team1_middle_run_rate'] if x['team1']==x['home_team'] else x['team2_middle_run_rate'], axis=1)
osum['home_death_run_rate'] = osum.apply(lambda x: x['team1_death_run_rate'] if x['team1']==x['home_team'] else x['team2_death_run_rate'], axis=1)

osum['away_pp_run_rate'] = osum.apply(lambda x: x['team1_pp_run_rate'] if x['team1']==x['away_team'] else x['team2_pp_run_rate'], axis=1)
osum['away_middle_run_rate'] = osum.apply(lambda x: x['team1_middle_run_rate'] if x['team1']==x['away_team'] else x['team2_middle_run_rate'], axis=1)
osum['away_death_run_rate'] = osum.apply(lambda x: x['team1_death_run_rate'] if x['team1']==x['away_team'] else x['team2_death_run_rate'], axis=1)

In [607]:
# osum['better_team'] = osum.apply(lambda x: x['team1'] if x['team1_runs'] > x['team2_runs'] else x['team2'], axis=1)

In [608]:
# osum['winner_new'] = osum.apply(lambda x: x['points'].split(" 2")[0] if "2" in x['points'] else (x['better_team'] if 'None' in x['points'] else "No Result/Draw"), axis=1)

In [712]:
team_long_names = {'Gujarat Titans':'GT','Kolkata Knight Riders': 'KKR', 'Delhi Capitals':'DC', 'Sunrisers Hyderabad':'SRH', 
'Royal Challengers Bangalore':'RCB', 'Lucknow Super Giants': 'LSG', 'Rajasthan Royals':'RR', 'Chennai Super Kings':'CSK', 
'Punjab Kings':'KXIP', 'Mumbai Indians':'MI', 'Kings XI Punjab':'KXIP', 'Delhi Daredevils':'DC', 'Rising Pune Supergiants':'RPS',
'Rising Pune Supergiant':'RPS','Gujarat Lions':'GT', 'Pune Warriors':'RPS', 
'Deccan Chargers':'SRH', 'Kochi Tuskers Kerala':'Kochi'}

In [713]:
osum['toss_won'] = osum['toss_won'].fillna('CSK')
osum['toss_won'] = osum['toss_won'].astype('string')
osum.replace({'toss_won': team_long_names}, inplace=True)
osum.replace({'winner': team_long_names}, inplace=True)

osum.replace({'winner': {'PBKS':'KXIP'}, 'toss_won':{'PBKS':'KXIP'}}, inplace=True)
osum.replace({'winner': {'GL':'GT'}, 'toss_won':{'GL':'GT'}}, inplace=True)
osum.replace({'winner': {'PWI':'RPS'}, 'toss_won':{'PWI':'RPS'}}, inplace=True)
# osum.replace({'winner': {'DD':'DC'}, 'toss_won':{'DD':'DC'}}, inplace=True)

In [714]:
# osum.replace({'winner_new':team_long_names}, inplace=True)

# osum.replace({'winner_new': {'PBKS':'KXIP'}, 'toss_won':{'PBKS':'KXIP'}}, inplace=True)
# osum.replace({'winner_new': {'GL':'GT'}, 'toss_won':{'GL':'GT'}}, inplace=True)
# osum.replace({'winner_new': {'PWI':'RPS'}, 'toss_won':{'PWI':'RPS'}}, inplace=True)
# osum.replace({'winner_new': {'DD':'DC'}, 'toss_won':{'DD':'DC'}}, inplace=True)

In [715]:
# # osum.replace({'winner_new':team_long_names}, inplace=True)

# osum.replace({'better_team': {'PBKS':'KXIP'}, 'toss_won':{'PBKS':'KXIP'}}, inplace=True)
# osum.replace({'better_team': {'GL':'GT'}, 'toss_won':{'GL':'GT'}}, inplace=True)
# osum.replace({'better_team': {'PWI':'RPS'}, 'toss_won':{'PWI':'RPS'}}, inplace=True)
# osum.replace({'better_team': {'DD':'DC'}, 'toss_won':{'DD':'DC'}}, inplace=True)

In [716]:
osum.toss_won.unique()

array(['RCB', 'CSK', 'RR', 'MI', 'SRH', 'KXIP', 'KKR', 'DC', 'Kochi',
       'RPS', 'GT', 'LSG'], dtype=object)

In [717]:
osum.winner.unique()

array(['KKR', 'CSK', 'DC', 'RCB', 'RR', 'KXIP', 'SRH', 'MI', 'RPS',
       'Kochi', 'GT', 'LSG'], dtype=object)

In [718]:
# osum['team1_runs_integrity']= osum.apply(lambda x: True if x['team1_runs'] == x['team1_pp_runs_scored'] + x['team1_middle_runs_scored'] + x['team1_death_runs_scored'] else False, axis =1)
# osum['team2_runs_integrity']= osum.apply(lambda x: True if x['team2_runs'] == x['team2_pp_runs_scored'] + x['team2_middle_runs_scored'] + x['team2_death_runs_scored'] else False, axis =1)

# osum['team2_wickets_integrity']= osum.apply(lambda x: True if x['team2_wickets'] == x['team2_pp_wickets_lost'] + x['team2_middle_wickets_lost'] + x['team2_death_wickets_lost'] else False, axis =1)
# osum['team1_wickets_integrity']= osum.apply(lambda x: True if x['team1_wickets'] == x['team1_pp_wickets_lost'] + x['team1_middle_wickets_lost'] + x['team1_death_wickets_lost'] else False, axis =1)

In [719]:
os_copy = osum.drop(['team2_overs', 'team1_overs', 
       # 'points_2023', 'winner', 'better_team',
       'team1_key_batters', 'team1_key_bowlers', 'team2_key_batters',
       'team2_key_bowlers', 'date', 'description', 'team1', 'team2',
       'team1_runs', 'team1_wickets', 'team2_runs', 'team2_wickets', 'result', 'live_score_link',
       'match_overs_link', 'team1_pp_runs_scored', 'team1_middle_runs_scored',
       'team1_death_runs_scored', 'team1_pp_wickets_lost',
       'team1_middle_wickets_lost', 'team1_death_wickets_lost',
       'team2_pp_runs_scored', 'team2_middle_runs_scored',
       'team2_death_runs_scored', 'team2_pp_wickets_lost',
       'team2_middle_wickets_lost', 'team2_death_wickets_lost', 
       'team1_pp_run_rate', 'team1_middle_run_rate', 'team1_death_run_rate',
       'team2_pp_run_rate', 'team2_middle_run_rate', 'team2_death_run_rate'], axis=1)
os_copy.rename(columns={'team1_score':'1st_innings_score', 'team2_score':'2nd_innings_score', 'winner_new':'winner'},inplace=True)

In [720]:
os_copy.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1007 entries, 0 to 61
Data columns (total 43 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   id                        1007 non-null   float64
 1   venue_name                1007 non-null   string 
 2   city                      1007 non-null   string 
 3   venue_id                  1007 non-null   string 
 4   decision                  1007 non-null   string 
 5   pom                       1007 non-null   string 
 6   1st_innings_score         1007 non-null   string 
 7   2nd_innings_score         1007 non-null   string 
 8   home_team                 1007 non-null   object 
 9   away_team                 1007 non-null   object 
 10  season                    1007 non-null   object 
 11  super_over                1007 non-null   object 
 12  points                    1007 non-null   string 
 13  toss_won                  1007 non-null   object 
 14  winner    

In [721]:
os_copy.to_csv('ipl_all_seasons_v6.csv', index=False)

In [565]:
driver.quit()